In [1]:
import os
import json
import datetime
import warnings
import polars as pl
import pandas as pd
import altair as alt

from src.najdi_rok import najdi_rok
from src.pocet_stran import pocet_stran
from src.bez_bordelu import bez_bordelu
from src.alt_friendly import alt_friendly
from src.hezke_jmeno import hezke_jmeno
from src.kristi_promin import kristi_promin
from src.me_to_neurazi import me_to_neurazi
from src.alt_friendly import alt_friendly

with open(os.path.join('src','kredity.json'), 'r', encoding='utf-8') as kredity:
    kredity = json.loads(kredity.read())
pl.Config(tbl_rows=100)
alt.data_transformers.disable_max_rows()
alt.themes.register('irozhlas', kristi_promin)
alt.themes.enable('irozhlas')
warnings.filterwarnings('ignore')

In [2]:
df = pl.read_parquet(os.path.join("data/cnb_sloupce","100.parquet"))
df = df.join(pl.read_parquet(os.path.join("data/cnb_sloupce","leader.parquet")), left_on="001", right_on="001", how="left")
df = df.join(pl.read_parquet(os.path.join("data/cnb_sloupce","008.parquet")), left_on="001", right_on="001", how="left")
df = df.to_pandas()
df = df[df["leader"].str[6].isin(["a", "t"])]
df = df[~df["leader"].str[7].isin(["b", "i", "s", " "])]
df = df[(df["008"].str[15:17] == "xr") & (df["008"].str[35:38] == "cze")]
df = pl.from_pandas(df)
df = df.join(pl.read_parquet(os.path.join("data/cnb_sloupce","022.parquet")), left_on="001", right_on="001", how="left")
df = df.join(pl.read_parquet(os.path.join("data/cnb_sloupce","245.parquet")), left_on="001", right_on="001", how="left")
df = df.join(pl.read_parquet(os.path.join("data/cnb_sloupce","300.parquet")), left_on="001", right_on="001", how="left")
df = df.join(pl.read_parquet(os.path.join("data/cnb_sloupce","655.parquet")), left_on="001", right_on="001", how="left")
df = df.join(pl.read_parquet(os.path.join("data/cnb_sloupce","700.parquet")), left_on="001", right_on="001", how="left")
df = df.explode("022_a").filter(pl.col("022_a").is_null())
df = df.with_columns(pl.col('008').map_elements(najdi_rok, return_dtype=int).alias('rok'))
df = df.with_columns(pl.col('300_a').map_elements(pocet_stran, return_dtype=int).alias('stran'))
df = df.with_columns(pl.col('245_a').map_elements(bez_bordelu, return_dtype=str))
df = df.explode('245_p').with_columns(pl.col('245_p').map_elements(bez_bordelu, return_dtype=str))
print(len(df))

716789


In [3]:
aut = pl.read_parquet(os.path.join("data","aut_vyber.parquet"))

In [4]:
df = df.filter(pl.col("rok") >= 1800)

In [5]:
print(len(df))

710142


In [6]:
df = df.filter((~pl.col("245_h").str.contains("grafika")) | pl.col("245_h").is_null()).unique(subset=["008","100_a","245_a","245_p"], keep="first")

In [7]:
print(len(df))

705921


In [8]:
nechcemejetam = [
    "jn20001103401",
    "xx0008006",
    "jn19990008769",
    "jx20060515016",
    "jn19981002230",
    "jn19981001737",
    "jn19990210182",
    "jn19990001842",
    "jn19990002786",
    "jn19990004346",
    "jn20020721077",
    "jn19990210513",
    "jn19990005488",
    "jo20000080627",
    "jn19990000171",
    "jn20001005715",
    "jn19981002409",
    "jn20000810141",
    "jn19981002129",
    "jn20001103529",
    "jn20000810032",
    "jn19990001513",
    "jx20040611003",
    "jn19990005499",
    "jn19981002230",
    "jn19990001907",
    "jo2005267810",
    "jo20241218643",
    "jn20000602144",
    "jn19990005454",
    "jn19981228078",
    "xx0010566",
    "jn20010310318",
    "xx0203193",
    "jn20001227589",
    "jo2003204270",
    "xx0082647",
    "jn19990001239"
]

# df = df.filter(~pl.col("100_7").is_in(nechcemejetam))

In [9]:
df.sample(10)

shape: (10, 68)
┌──────────┬─────────────────────────────────┬───────────────┬───────────┬───┬───────────┬───────────┬──────┬───────┐
│ 100_ind1 ┆ 100_a                           ┆ 100_7         ┆ 100_4     ┆ … ┆ 700_9     ┆ 700_g     ┆ rok  ┆ stran │
│ ---      ┆ ---                             ┆ ---           ┆ ---       ┆   ┆ ---       ┆ ---       ┆ ---  ┆ ---   │
│ str      ┆ str                             ┆ str           ┆ list[str] ┆   ┆ list[str] ┆ list[str] ┆ i64  ┆ i64   │
╞══════════╪═════════════════════════════════╪═══════════════╪═══════════╪═══╪═══════════╪═══════════╪══════╪═══════╡
│ 1        ┆ Bláhová, Dagmar,                ┆ jn20000400202 ┆ ["aut"]   ┆ … ┆ null      ┆ null      ┆ 2006 ┆ 119   │
│ 1        ┆ Cempírková, Soňa                ┆ jo2014802135  ┆ ["aut"]   ┆ … ┆ null      ┆ null      ┆ 2015 ┆ 167   │
│ 1        ┆ Kincl, Miloslav,                ┆ jk01060174    ┆ ["aut"]   ┆ … ┆ null      ┆ null      ┆ 1970 ┆ 163   │
│ 1        ┆ Müller, Karel,                  ┆ jo20010087059 ┆ ["aut"]   ┆ … ┆ null      ┆ null      ┆ 1973 ┆ 115   │
│ 1        ┆ Velenský, Michael,              ┆ jn19990010018 ┆ ["aut"]   ┆ … ┆ null      ┆ null      ┆ 1999 ┆ 62    │
│ 1        ┆ Hanus, Stanislav,               ┆ jn20000710046 ┆ ["aut"]   ┆ … ┆ null      ┆ null      ┆ 1982 ┆ 135   │
│ 1        ┆ Šindler, Jaroslav               ┆ null          ┆ ["aut"]   ┆ … ┆ null      ┆ null      ┆ 1971 ┆ 30    │
│ 1        ┆ Dostojevskij, Fedor Michajlovi… ┆ jn19990210182 ┆ ["aut"]   ┆ … ┆ null      ┆ null      ┆ 2013 ┆ 981   │
│ 1        ┆ Lilley, Samuel                  ┆ null          ┆ ["aut"]   ┆ … ┆ null      ┆ null      ┆ 1973 ┆ 547   │
│ 1        ┆ Veselský, Petr Miloslav,        ┆ jk01142116    ┆ ["aut"]   ┆ … ┆ null      ┆ null      ┆ 1854 ┆ 45    │
└──────────┴─────────────────────────────────┴───────────────┴───────────┴───┴───────────┴───────────┴──────┴───────┘

In [10]:
df = df.drop_nulls(subset=["700_a","700_4","700_7"]).explode(["700_a","700_4","700_7"])

In [11]:
df.select(pl.col(["700_a","700_4","700_7",'245_a'])).sample(10)

shape: (10, 4)
┌───────────────────┬───────┬───────────────┬─────────────────────────────────┐
│ 700_a             ┆ 700_4 ┆ 700_7         ┆ 245_a                           │
│ ---               ┆ ---   ┆ ---           ┆ ---                             │
│ str               ┆ str   ┆ str           ┆ str                             │
╞═══════════════════╪═══════╪═══════════════╪═════════════════════════════════╡
│ Andělová, Eliška, ┆ ill   ┆ xx0237138     ┆ O nebi a zemi, aneb, Meteorolo… │
│ Biały, Witold,    ┆ aut   ┆ mzk2008473156 ┆ Těžba uhlí a posthornická kraj… │
│ Jandová, Ludmila, ┆ ill   ┆ jn19990216077 ┆ Křížová cesta Maxmiliána Maria… │
│ Selman, Sarah     ┆ aut   ┆ jx20091102017 ┆ Navigační cvičení RYA           │
│ Bláha, Václav,    ┆ art   ┆ jk01012210    ┆ Hlavou dolů                     │
│ Pešek, Jiří,      ┆ aut   ┆ jk01092639    ┆ Litostratigrafické členění stř… │
│ Kadlec, Josef,    ┆ aui   ┆ jk01052433    ┆ Setkání s minulostí             │
│ Havránková, Ruda, ┆ trl   ┆ jk01040449    ┆ Neobyčejné příhody              │
│ Vrbová, Hana,     ┆ aft   ┆ jk01151014    ┆ Dobrodružství na dně moří       │
│ Čapek, Karel,     ┆ null  ┆ aun2007415079 ┆ Dramata                         │
└───────────────────┴───────┴───────────────┴─────────────────────────────────┘

## Autorské spolupráce

In [13]:
from itertools import combinations

In [14]:
def find_collaborations(df):
    # Filter for authors only
    authors = df.filter(pl.col('700_4') == 'aut')
    
    # Group by book title to get authors per book
    books_authors = authors.group_by('245_a').agg(pl.col('700_a').alias('authors'))
    
    # Generate author pairs and count collaborations
    collaborations = []
    for book in books_authors.iter_rows():
        if len(book[1]) > 1:  # Only consider books with multiple authors
            for pair in combinations(sorted(book[1]), 2):
                collaborations.append(pair)
    
    # Convert to dataframe and count frequencies
    collab_df = pl.DataFrame({
        'author1': [p[0] for p in collaborations],
        'author2': [p[1] for p in collaborations]
    })
    
    if len(collab_df) == 0:
        return pl.DataFrame({'author1': [], 'author2': [], 'collaboration_count': []})
    
    return (collab_df.group_by(['author1', 'author2'])
            .count()
            .sort('count', descending=True)
            .rename({'count': 'collaboration_count'}))

In [15]:
find_collaborations(df).filter(pl.col("author1") != pl.col("author2"))

shape: (222_858, 3)
┌─────────────────────────┬───────────────────────────┬─────────────────────┐
│ author1                 ┆ author2                   ┆ collaboration_count │
│ ---                     ┆ ---                       ┆ ---                 │
│ str                     ┆ str                       ┆ u32                 │
╞═════════════════════════╪═══════════════════════════╪═════════════════════╡
│ Novotný, Miloš          ┆ Novák, František          ┆ 1165                │
│ Král, Lukáš             ┆ Valenta, Tomáš            ┆ 1156                │
│ Krupka, Peter,          ┆ Nechvátalová, Jana,       ┆ 1089                │
│ Malý, Martin            ┆ Münch, Otto               ┆ 897                 │
│ Münch, Otto             ┆ Čechová, Jarmila          ┆ 826                 │
│ Frydryšková, Yvetta     ┆ Münch, Otto               ┆ 820                 │
│ Nechvátalová, Jana,     ┆ Staudková, Hana           ┆ 792                 │
│ Krupka, Peter,          ┆ Staudková, Hana           ┆ 792                 │
│ Medek, Jaroslav,        ┆ Petrůj, Svatopluk,        ┆ 761                 │
│ Frydryšková, Yvetta     ┆ Čechová, Jarmila          ┆ 730                 │
│ Hrdinová, Jarmila       ┆ Novák, František          ┆ 636                 │
│ Nechvátalová, Jana,     ┆ Tůmová, Věra              ┆ 594                 │
│ Krupka, Peter,          ┆ Tůmová, Věra              ┆ 594                 │
│ Kulík, Oldřich          ┆ Tláskal, Jaromír,         ┆ 583                 │
│ Krupka, Peter,          ┆ Pišl, Milan,              ┆ 495                 │
│ Nechvátalová, Jana,     ┆ Pišl, Milan,              ┆ 495                 │
│ Čupera, Jiří,           ┆ Ždánský, Bronislav        ┆ 468                 │
│ Krupka, Peter,          ┆ Rektorys, Karel,          ┆ 462                 │
│ Nechvátalová, Jana,     ┆ Rektorys, Karel,          ┆ 462                 │
│ Staudková, Hana         ┆ Tůmová, Věra              ┆ 438                 │
│ Jirák, Antonín,         ┆ Reitler, Antonín,         ┆ 390                 │
│ Lokay, Bohumil          ┆ Štolba, František         ┆ 387                 │
│ Pišl, Milan,            ┆ Staudková, Hana           ┆ 360                 │
│ Rektorys, Karel,        ┆ Staudková, Hana           ┆ 336                 │
│ Kubát, Jindřich         ┆ Ždánský, Bronislav        ┆ 315                 │
│ Hájek, Bohumil,         ┆ Otčenášek, Ladislav       ┆ 289                 │
│ Styblík, Vlastimil,     ┆ Šafránek, František       ┆ 272                 │
│ Doležalová, Alena Bára  ┆ Novák, František          ┆ 270                 │
│ Pišl, Milan,            ┆ Tůmová, Věra              ┆ 270                 │
│ Krsička, Rudolf         ┆ Ondráček, Josef           ┆ 256                 │
│ Chromá, Danuše          ┆ Münch, Otto               ┆ 255                 │
│ Rektorys, Karel,        ┆ Tůmová, Věra              ┆ 252                 │
│ Tožička, Bohumil,       ┆ Žofková, Lidmila,         ┆ 248                 │
│ Barborová, Lenka        ┆ Münch, Otto               ┆ 245                 │
│ Krupka, Peter,          ┆ Vřešťál, Evžen            ┆ 231                 │
│ Krupka, Peter,          ┆ Černá, Milada             ┆ 231                 │
│ Nechvátalová, Jana,     ┆ Vřešťál, Evžen            ┆ 231                 │
│ Nechvátalová, Jana,     ┆ Černá, Milada             ┆ 231                 │
│ Jelínková, Anna         ┆ Košťálová, Marie          ┆ 224                 │
│ Hechtová, Marie,        ┆ Košťálová, Marie          ┆ 224                 │
│ Hrdinová, Jarmila       ┆ Novotný, Miloš            ┆ 220                 │
│ Nykl, Jaroslav,         ┆ Rottová, Milada,          ┆ 216                 │
│ Chalupa, Petr,          ┆ Hübelová, Dana,           ┆ 212                 │
│ Červený, František,     ┆ Řehořovský, Václav Karel, ┆ 211                 │
│ Pišl, Milan,            ┆ Rektorys, Karel,          ┆ 211                 │
│ Hampl, Rudolf,          ┆ Úlehla, Josef,            ┆ 210                 │
│ 

In [16]:
df_autorske = df.filter(pl.col('700_4') == 'aut')

In [17]:
def hezkejmeno(sto):
    if not sto[-1].isalnum():
        sto = sto[:-1]
    if "," in sto:
        sto = sto.split(",")
        sto = sto[1].strip() + " " + sto[0].strip()
    return sto    

In [18]:
df_autorske = df_autorske.with_columns(pl.col("100_a").map_elements(hezkejmeno).alias("jmeno1")).with_columns(pl.col("700_a").map_elements(hezkejmeno).alias("jmeno2"))

In [19]:
df_autorske

shape: (164_619, 70)
┌──────────┬──────────────────┬────────────────┬────────────────┬───┬──────┬───────┬─────────────────┬─────────────────┐
│ 100_ind1 ┆ 100_a            ┆ 100_7          ┆ 100_4          ┆ … ┆ rok  ┆ stran ┆ jmeno1          ┆ jmeno2          │
│ ---      ┆ ---              ┆ ---            ┆ ---            ┆   ┆ ---  ┆ ---   ┆ ---             ┆ ---             │
│ str      ┆ str              ┆ str            ┆ list[str]      ┆   ┆ i64  ┆ i64   ┆ str             ┆ str             │
╞══════════╪══════════════════╪════════════════╪════════════════╪═══╪══════╪═══════╪═════════════════╪═════════════════╡
│ 1        ┆ Dupač, Václav,   ┆ jk01023327     ┆ ["aut"]        ┆ … ┆ 1980 ┆ 134   ┆ Václav Dupač    ┆ Jitka Dupačová  │
│ 1        ┆ Rožek, Filip,    ┆ hka20191055983 ┆ ["aut"]        ┆ … ┆ 2022 ┆ 109   ┆ Filip Rožek     ┆ Lukáš Fišer     │
│ 1        ┆ Rožek, Filip,    ┆ hka20191055983 ┆ ["aut"]        ┆ … ┆ 2022 ┆ 109   ┆ Filip Rožek     ┆ F. A. Brabec    │
│ 1        ┆ Řehoř, Jan,      ┆ jk01110048     ┆ ["aut"]        ┆ … ┆ 1964 ┆ 443   ┆ Jan Řehoř       ┆ Jindřich Groh   │
│ 1        ┆ Řehoř, Jan,      ┆ jk01110048     ┆ ["aut"]        ┆ … ┆ 1964 ┆ 443   ┆ Jan Řehoř       ┆ František       │
│          ┆                  ┆                ┆                ┆   ┆      ┆       ┆                 ┆ Černík          │
│ 1        ┆ Gerard-Sharp,    ┆ xx0000921      ┆ ["aut"]        ┆ … ┆ 2002 ┆ 384   ┆ Lisa            ┆ Tim Perry       │
│          ┆ Lisa             ┆                ┆                ┆   ┆      ┆       ┆ Gerard-Sharp    ┆                 │
│ 1        ┆ Wolf, Jochen     ┆ uzp2009504217  ┆ ["aut"]        ┆ … ┆ 2012 ┆ 13    ┆ Jochen Wolf     ┆ Marie Wolfová   │
│ 1        ┆ Lakosil, Jan,    ┆ ola2007404683  ┆ ["aut"]        ┆ … ┆ 2010 ┆ 309   ┆ Jan Lakosil     ┆ Tomáš Svoboda   │
│ 1        ┆ Lakosil, Jan,    ┆ ola2007404683  ┆ ["aut"]        ┆ … ┆ 2010 ┆ 309   ┆ Jan Lakosil     ┆ Ladislav Čermák │
│ 1        ┆ Wallenfelsová,   ┆ null           ┆ ["aut"]        ┆ … ┆ 1987 ┆ 107   ┆ Helena          ┆ Antonín Valder  │
│          ┆ Helena           ┆                ┆                ┆   ┆      ┆       ┆ Wallenfelsová   ┆                 │
│ 1        ┆ Walker, Richard, ┆ xx0007559      ┆ ["aut"]        ┆ … ┆ 2003 ┆ 304   ┆ Richard Walker  ┆ David Burnie    │
│ 1        ┆ Horáček, Radek,  ┆ jk01042026     ┆ ["aut"]        ┆ … ┆ 2019 ┆ 111   ┆ Radek Horáček   ┆ Blahoslav       │
│          ┆                  ┆                ┆                ┆   ┆      ┆       ┆                 ┆ Rozbořil        │
│ 1        ┆ Horáček, Radek,  ┆ jk01042026     ┆ ["aut"]        ┆ … ┆ 2019 ┆ 111   ┆ Radek Horáček   ┆ Hana Stehlíková │
│          ┆                  ┆                ┆                ┆   ┆      ┆       ┆                 ┆ Babyrádová      │
│ 1        ┆ Volka, Karel,    ┆ jn20001103525  ┆ ["aut"]        ┆ … ┆ 2006 ┆ 100   ┆ Karel Volka     ┆ Marcela         │
│          ┆                  ┆                ┆                ┆   ┆      ┆       ┆                 ┆ Tkadlecová      │
│ 1        ┆ Volka, Karel,    ┆ jn20001103525  ┆ ["aut"]        ┆ … ┆ 2006 ┆ 100   ┆ Karel Volka     ┆ Kamil Záruba    │
│ 1        ┆ Angelovská,      ┆ mzk2006324010  ┆ ["aut"]        ┆ … ┆ 2009 ┆ 340   ┆ Olga Angelovská ┆ Pavol Frič      │
│          ┆ Olga,            ┆                ┆                ┆   ┆      ┆       ┆                 ┆                 │
│ 1        ┆ Angelovská,      ┆ mzk2006324010  ┆ ["aut"]        ┆ … ┆ 2009 ┆ 340   ┆ Olga Angelovská ┆ Rochdi Goulli   │
│          ┆ Olga,            ┆                ┆                ┆   ┆      ┆       ┆                 ┆                 │
│ 1        ┆ Dvořáková, Dana  ┆ jo2003197096   ┆ ["aut"]        ┆ … ┆ 2017 ┆ 1     ┆ Dana Dvořáková  ┆ Libuše Kubová   │
│ 1        ┆ Osborne, John,   ┆ xx0214461      ┆ ["aut"]        ┆ … ┆ 1963 ┆ 110   ┆ John Osborne    ┆ Anthony         │
│          ┆                  ┆                ┆                ┆   ┆      ┆       ┆                 ┆ Crei

In [20]:
def kombajmen(jmeno1, jmeno2, radit=True, spojeni = "a"):
    try:
        jmena = [jmeno1.split(" ")[-1], jmeno2.split(" ")[-1]]
        if radit == True:
            jmena.sort()
        return f" {spojeni} ".join(jmena)
    except Exception as e:
        print(e)
        return None

In [21]:
df_autorske = df_autorske.with_columns(pl.struct('jmeno1','jmeno2').map_elements(lambda x: kombajmen(x['jmeno1'], x['jmeno2'])).alias("dvojice"))

In [22]:
df_autorske.group_by(['dvojice']).agg(pl.col("245_a").n_unique()).sort(by="245_a",descending=True)

shape: (105_346, 2)
┌─────────────────────────────┬───────┐
│ dvojice                     ┆ 245_a │
│ ---                         ┆ ---   │
│ str                         ┆ u32   │
╞═════════════════════════════╪═══════╡
│ David a Soukup              ┆ 126   │
│ Nedbalová a Nedbalová       ┆ 90    │
│ Engels a Marx               ┆ 60    │
│ Benešová a Formáčková       ┆ 52    │
│ Benešová a Kanyzová         ┆ 52    │
│ Benešová a Příhoda          ┆ 52    │
│ Benešová a Fukalová         ┆ 52    │
│ Benešová a Vondrák          ┆ 52    │
│ Benešová a Šmíd             ┆ 52    │
│ Mihulová a Svoboda          ┆ 43    │
│ Brožová a Vostrá            ┆ 38    │
│ Smíšek a Smíšková           ┆ 36    │
│ Nedbalcová a Zouharová      ┆ 36    │
│ Voskovec a Werich           ┆ 35    │
│ Polášek a Polášková         ┆ 35    │
│ Jirotka a Vaněk             ┆ 34    │
│ Kučera a Stach              ┆ 33    │
│ Grimm a Grimm               ┆ 33    │
│ Child a Preston             ┆ 32    │
│ David a Dobrovolná          ┆ 31    │
│ Chmelař a Šimon             ┆ 29    │
│ Goscinny a Morris           ┆ 29    │
│ Kubálek a Kubálková         ┆ 28    │
│ Klečka a Kunz               ┆ 28    │
│ Kozák a Roček               ┆ 27    │
│ Hošková a Paprčka           ┆ 26    │
│ Jirotka a Turková           ┆ 26    │
│ Lenin a Marx                ┆ 26    │
│ Rusňáková a Sedláček        ┆ 25    │
│ Augusta a Honzák            ┆ 25    │
│ Bartoňová a Vítková         ┆ 25    │
│ Beran a Cílek               ┆ 25    │
│ Pešatová a Švingalová       ┆ 25    │
│ Novák a Taterová            ┆ 25    │
│ Bruthans a Kondrová         ┆ 24    │
│ Pecinovský a Pecinovský     ┆ 24    │
│ Bruthans a Bůzek            ┆ 24    │
│ Strugackij a Strugackij     ┆ 23    │
│ Erben a Němcová             ┆ 23    │
│ Jucovičová a Žáčková        ┆ 23    │
│ Bruthans a Kadlecová        ┆ 23    │
│ Mikulenková a Molnár        ┆ 22    │
│ Beran a Jirotka             ┆ 22    │
│ Novák a Špička              ┆ 22    │
│ Čadilová a Žampachová       ┆ 21    │
│ Müller a Müllerová          ┆ 21    │
│ Erben a Vilikovský          ┆ 21    │
│ Matiašková a Nedbalcová     ┆ 21    │
│ Beran a Vaněk               ┆ 21    │
│ Bratršovská a Hrdlička      ┆ 21    │
│ …                           ┆ …     │
│ Jirásek a Žlab              ┆ 1     │
│ Křížek a Šíma               ┆ 1     │
│ Janál a Štětina             ┆ 1     │
│ Loiseau a Pincas            ┆ 1     │
│ Ellefson a Popoff           ┆ 1     │
│ Beneš a Kokaisl             ┆ 1     │
│ Jičínský a Sucharda         ┆ 1     │
│ Baronová a Koubová          ┆ 1     │
│ Bai a Hayan                 ┆ 1     │
│ Blabolilová a Hůla          ┆ 1     │
│ Koutný a Skoupil            ┆ 1     │
│ Fořterová a Süss            ┆ 1     │
│ Marková a Straková          ┆ 1     │
│ >>Sternbergu a >>Šternberka ┆ 1     │
│ Dvorský a Slabý             ┆ 1     │
│ Dvořák a Suchomel           ┆ 1     │
│ Frič a Laube                ┆ 1     │
│ Odvody a Pajer              ┆ 1     │
│ Dvořák a Majer              ┆ 1     │
│ Bakal a Šaripov             ┆ 1     │
│ Handl a Klaus               ┆ 1     │
│ Jaeglé a Valkova            ┆ 1     │
│ Blatná a Dobšíčková         ┆ 1     │
│ D‘jačenko a Merzljak        ┆ 1     │
│ Dolejšová a Šolc            ┆ 1     │
│ Hájková a Miksová           ┆ 1     │
│ Pôbiš a Žaba                ┆ 1     │
│ Petříček a Trs              ┆ 1     │
│ Fricová a Votava            ┆ 1     │
│ Drtinová a Horáček          ┆ 1     │
│ Gorbačev a Jurgens          ┆ 1     │
│ Danny a Málek               ┆ 1     │
│ Fryček a Královec           ┆ 1     │
│ Domin a Vitásek             ┆ 1     │
│ Chrpová a Slavíková         ┆ 1     │
│ Pátek a Tvrdek              ┆ 1     │
│ Bude a Hrdý                 ┆ 1     │
│ Karel a Kinský              ┆ 1     │
│ Pollio a Pollux             ┆ 1     │
│ Kalina a Klimeš             ┆ 1     │
│ Děták a Melicharová         ┆ 1     │
│ Andersson a Olsson          ┆ 1     │
│ Taufer a Toman              ┆ 1     │
│ Benátský a Kulevit

In [23]:
df_autorske.group_by(['100_a','100_7','700_a']).agg(pl.col("245_a").n_unique()).sort(by="245_a",descending=True)

shape: (111_462, 4)
┌─────────────────────────────────┬────────────────┬──────────────────────────────┬───────┐
│ 100_a                           ┆ 100_7          ┆ 700_a                        ┆ 245_a │
│ ---                             ┆ ---            ┆ ---                          ┆ ---   │
│ str                             ┆ str            ┆ str                          ┆ u32   │
╞═════════════════════════════════╪════════════════╪══════════════════════════════╪═══════╡
│ David, Petr,                    ┆ xx0006786      ┆ Soukup, Vladimír,            ┆ 126   │
│ Nedbalová, Marie                ┆ jo2014816080   ┆ Nedbalová, Josefína          ┆ 87    │
│ Marx, Karl,                     ┆ jn19990005454  ┆ Engels, Friedrich,           ┆ 59    │
│ Benešová, Hana,                 ┆ pna2012702164  ┆ Vondrák, Jan,                ┆ 52    │
│ Benešová, Hana,                 ┆ pna2012702164  ┆ Příhoda, Pavel,              ┆ 52    │
│ Benešová, Hana,                 ┆ pna2012702164  ┆ Formáčková, Marie,           ┆ 52    │
│ Benešová, Hana,                 ┆ pna2012702164  ┆ Kanyzová, Žofie,             ┆ 52    │
│ Benešová, Hana,                 ┆ pna2012702164  ┆ Fukalová, Lenka              ┆ 52    │
│ Benešová, Hana,                 ┆ pna2012702164  ┆ Šmíd, Václav,                ┆ 52    │
│ Mihulová, Marie,                ┆ jn20001227798  ┆ Svoboda, Milan               ┆ 43    │
│ Vostrá, Markéta                 ┆ js20050801018  ┆ Brožová, Marie,              ┆ 38    │
│ Smíšek, Richard,                ┆ xx0038627      ┆ Smíšková, Kateřina,          ┆ 36    │
│ Smíšek, Richard,                ┆ xx0038627      ┆ Smíšková, Zuzana             ┆ 36    │
│ Nedbalcová, Kateřina            ┆ mzk2015871497  ┆ Zouharová, Monika            ┆ 33    │
│ Grimm, Jacob Ludwig Karl,       ┆ jn19981228078  ┆ Grimm, Wilhelm Karl,         ┆ 32    │
│ Preston, Douglas J.,            ┆ jn20000810185  ┆ Child, Lincoln,              ┆ 32    │
│ Voskovec, Jiří,                 ┆ jk01150746     ┆ Werich, Jan,                 ┆ 32    │
│ David, Petr,                    ┆ xx0006786      ┆ Dobrovolná, Věra,            ┆ 30    │
│ Morris,                         ┆ xx0038205      ┆ Goscinny, René,              ┆ 29    │
│ Jirotka, Antonín,               ┆ jx20040623006  ┆ Vaněk, Jan J.,               ┆ 29    │
│ Klečka, Antonín,                ┆ jk01060331     ┆ Kunz, Emil,                  ┆ 28    │
│ Chmelař, František,             ┆ jk01050240     ┆ Šimon, Jaroslav,             ┆ 27    │
│ Kozák, Jan,                     ┆ jk01062553     ┆ Roček, Jan,                  ┆ 26    │
│ Stach, Jan,                     ┆ jn20010309343  ┆ Kučera, Miroslav,            ┆ 26    │
│ Marx, Karl,                     ┆ jn19990005454  ┆ Lenin, Vladimir Il‘jič,      ┆ 26    │
│ Paprčka, Milan,                 ┆ osa2014838884  ┆ Hošková, Martina,            ┆ 26    │
│ Bartoňová, Miroslava,           ┆ mzk2004148531  ┆ Vítková, Marie,              ┆ 25    │
│ Bruthans, Jiří                  ┆ jx20090211004  ┆ Kondrová, Lucie,             ┆ 24    │
│ Polášková, Jiřina,              ┆ jn20000402028  ┆ Polášek, Jaromír,            ┆ 24    │
│ Bruthans, Jiří                  ┆ jx20090211004  ┆ Bůzek, František             ┆ 24    │
│ Augusta, Pavel,                 ┆ jk01010424     ┆ Honzák, František,           ┆ 24    │
│ Kubálek, Tomáš,                 ┆ jo2002103223   ┆ Kubálková, Markéta,          ┆ 23    │
│ Strugackij, Arkadij Natanovič,  ┆ jn19990210589  ┆ Strugackij, Boris Natanovič, ┆ 23    │
│ Taterová, Milada                ┆ jk01132074     ┆ Novák, Jiří,                 ┆ 23    │
│ Jirotka, Antonín,               ┆ jx20040623006  ┆ Turková, Zoja,               ┆ 22    │
│ Bruthans, Jiří                  ┆ jx20090211004  ┆ Kadlecová, Renáta            ┆ 22    │
│ Patterson, James,               ┆ jo20000076489  ┆ Paetro, Maxine,              ┆ 21    │
│ Nedbalcová, Kateřina            ┆ mzk2015871497  ┆ Matiašková, Katarína         ┆ 21    │
│ Bruthans, Jiří        

In [24]:
df.filter(pl.col("700_a") == "Soukup, Vladimír,").filter(pl.col("100_a") == "David, Petr,")

shape: (197, 68)
┌──────────┬──────────────┬───────────┬────────────────┬───┬───────────┬───────────┬──────┬───────┐
│ 100_ind1 ┆ 100_a        ┆ 100_7     ┆ 100_4          ┆ … ┆ 700_9     ┆ 700_g     ┆ rok  ┆ stran │
│ ---      ┆ ---          ┆ ---       ┆ ---            ┆   ┆ ---       ┆ ---       ┆ ---  ┆ ---   │
│ str      ┆ str          ┆ str       ┆ list[str]      ┆   ┆ list[str] ┆ list[str] ┆ i64  ┆ i64   │
╞══════════╪══════════════╪═══════════╪════════════════╪═══╪═══════════╪═══════════╪══════╪═══════╡
│ 1        ┆ David, Petr, ┆ xx0006786 ┆ ["aut"]        ┆ … ┆ null      ┆ null      ┆ 2005 ┆ 175   │
│ 1        ┆ David, Petr, ┆ xx0006786 ┆ ["aut"]        ┆ … ┆ null      ┆ null      ┆ 2012 ┆ 232   │
│ 1        ┆ David, Petr, ┆ xx0006786 ┆ ["aut"]        ┆ … ┆ null      ┆ null      ┆ 2004 ┆ 191   │
│ 1        ┆ David, Petr, ┆ xx0006786 ┆ ["aut"]        ┆ … ┆ null      ┆ null      ┆ 2001 ┆ 154   │
│ 1        ┆ David, Petr, ┆ xx0006786 ┆ ["aut"]        ┆ … ┆ null      ┆ null      ┆ 2015 ┆ 219   │
│ 1        ┆ David, Petr, ┆ xx0006786 ┆ ["aut"]        ┆ … ┆ null      ┆ null      ┆ 2008 ┆ 399   │
│ 1        ┆ David, Petr, ┆ xx0006786 ┆ ["aut"]        ┆ … ┆ null      ┆ null      ┆ 2002 ┆ 119   │
│ 1        ┆ David, Petr, ┆ xx0006786 ┆ ["aut"]        ┆ … ┆ null      ┆ null      ┆ 2017 ┆ 432   │
│ 1        ┆ David, Petr, ┆ xx0006786 ┆ ["aut"]        ┆ … ┆ null      ┆ null      ┆ 2022 ┆ 408   │
│ 1        ┆ David, Petr, ┆ xx0006786 ┆ ["aut"]        ┆ … ┆ null      ┆ null      ┆ 2023 ┆ 239   │
│ 1        ┆ David, Petr, ┆ xx0006786 ┆ ["aut", "pht"] ┆ … ┆ null      ┆ null      ┆ 2016 ┆ 384   │
│ 1        ┆ David, Petr, ┆ xx0006786 ┆ ["aut"]        ┆ … ┆ null      ┆ null      ┆ 2001 ┆ 128   │
│ 1        ┆ David, Petr, ┆ xx0006786 ┆ ["aut"]        ┆ … ┆ null      ┆ null      ┆ 2005 ┆ 232   │
│ 1        ┆ David, Petr, ┆ xx0006786 ┆ ["aut"]        ┆ … ┆ null      ┆ null      ┆ 1999 ┆ 134   │
│ 1        ┆ David, Petr, ┆ xx0006786 ┆ ["aut"]        ┆ … ┆ null      ┆ null      ┆ 2005 ┆ 135   │
│ 1        ┆ David, Petr, ┆ xx0006786 ┆ ["aut"]        ┆ … ┆ null      ┆ null      ┆ 2011 ┆ 380   │
│ 1        ┆ David, Petr, ┆ xx0006786 ┆ ["aut"]        ┆ … ┆ null      ┆ null      ┆ 2007 ┆ 141   │
│ 1        ┆ David, Petr, ┆ xx0006786 ┆ ["aut"]        ┆ … ┆ null      ┆ null      ┆ 2000 ┆ 147   │
│ 1        ┆ David, Petr, ┆ xx0006786 ┆ ["aut"]        ┆ … ┆ null      ┆ null      ┆ 2016 ┆ 207   │
│ 1        ┆ David, Petr, ┆ xx0006786 ┆ ["aut"]        ┆ … ┆ null      ┆ null      ┆ 2004 ┆ 191   │
│ 1        ┆ David, Petr, ┆ xx0006786 ┆ ["aut"]        ┆ … ┆ null      ┆ null      ┆ 2009 ┆ 232   │
│ 1        ┆ David, Petr, ┆ xx0006786 ┆ ["aut"]        ┆ … ┆ null      ┆ null      ┆ 2000 ┆ 135   │
│ 1        ┆ David, Petr, ┆ xx0006786 ┆ ["aut"]        ┆ … ┆ null      ┆ null      ┆ 1998 ┆ 159   │
│ 1        ┆ David, Petr, ┆ xx0006786 ┆ ["aut"]        ┆ … ┆ null      ┆ null      ┆ 2011 ┆ 416   │
│ 1        ┆ David, Petr, ┆ xx0006786 ┆ ["aut"]        ┆ … ┆ null      ┆ null      ┆ 2010 ┆ 384   │
│ 1        ┆ David, Petr, ┆ xx0006786 ┆ ["aut"]        ┆ … ┆ null      ┆ null      ┆ 2003 ┆ 143   │
│ 1        ┆ David, Petr, ┆ xx0006786 ┆ ["aut"]        ┆ … ┆ null      ┆ null      ┆ 2002 ┆ 157   │
│ 1        ┆ David, Petr, ┆ xx0006786 ┆ ["aut"]        ┆ … ┆ null      ┆ null      ┆ 2010 ┆ 384   │
│ 1        ┆ David, Petr, ┆ xx0006786 ┆ ["aut"]        ┆ … ┆ null      ┆ null      ┆ 2009 ┆ 328   │
│ 1        ┆ David, Petr, ┆ xx0006786 ┆ ["aut"]        ┆ … ┆ null      ┆ null      ┆ 2012 ┆ 199   │
│ 1        ┆ David, Petr, ┆ xx0006786 ┆ ["aut"]        ┆ … ┆ null      ┆ null      ┆ 2016 ┆ 207   │
│ 1        ┆ David, Petr, ┆ xx0006786 ┆ ["aut"]        ┆ … ┆ null      ┆ null      ┆ 1994 ┆ 63    │
│ 1        ┆ David, Petr, ┆ xx0006786 ┆ ["aut"]        ┆ … ┆ null      ┆ null      ┆ 2001 ┆ 133   │
│ 1        ┆ David, Petr, ┆ xx0006786 ┆ ["aut"]        ┆ … ┆ null      ┆ null      ┆ 2000 ┆ 99    │
│ 1        ┆ David, Petr, ┆ xx0006786 ┆ ["aut"]        ┆ … ┆ null      ┆ null      

## Ilustrátorstvo

In [26]:
df_ill = df.filter(pl.col('700_4') == 'ill')

In [27]:
df_ill = df_ill.with_columns(pl.col("100_a").map_elements(hezkejmeno).alias("jmeno1")).with_columns(pl.col("700_a").map_elements(hezkejmeno).alias("jmeno2"))

In [28]:
df_ill = df_ill.with_columns(pl.struct('jmeno1','jmeno2').map_elements(lambda x: kombajmen(x['jmeno1'], x['jmeno2'], radit=False, spojeni="&")).alias("dvojice"))

In [29]:
df_ill.filter(~pl.col("100_7").is_in(nechcemejetam)).group_by(['dvojice']).agg(pl.col("245_a").n_unique()).sort(by="245_a",descending=True)

shape: (32_296, 2)
┌─────────────────────────────┬───────┐
│ dvojice                     ┆ 245_a │
│ ---                         ┆ ---   │
│ str                         ┆ u32   │
╞═════════════════════════════╪═══════╡
│ Štíplová & Němeček          ┆ 108   │
│ Nedbalová & Popprová        ┆ 87    │
│ Nedbalová & Poppr           ┆ 68    │
│ Bass & Kratochvíl           ┆ 67    │
│ Švandrlík & Winter-Neprakta ┆ 64    │
│ Čapek & Čapek               ┆ 33    │
│ Pospíšilová & Trsťan        ┆ 31    │
│ Hašek & Lada                ┆ 30    │
│ Rosecká & Růžička           ┆ 28    │
│ Pospíšilová & Vopičková     ┆ 25    │
│ Škodová & Kubašta           ┆ 25    │
│ Foglar & Čermák             ┆ 24    │
│ Čtvrtek & Pilař             ┆ 24    │
│ Piroddi & Baruzzi           ┆ 23    │
│ Tetourová & Plicková        ┆ 23    │
│ Macourek & Born             ┆ 22    │
│ Bednářová & Šmarda          ┆ 21    │
│ Drijverová & Otčenášek      ┆ 21    │
│ Žáček & Born                ┆ 21    │
│ Válková & Kopl              ┆ 21    │
│ Šavlíková & Roverová        ┆ 20    │
│ Pospíšilová & Vydrová       ┆ 19    │
│ Webb & Williams             ┆ 19    │
│ Steklač & Born              ┆ 19    │
│ Walliams & Ross             ┆ 19    │
│ Grey & Hora                 ┆ 19    │
│ Stará & Starý               ┆ 19    │
│ Kratochvíl & Vydrová        ┆ 19    │
│ Wenig & Wenig               ┆ 18    │
│ Felix & Hísek               ┆ 18    │
│ Dahl & Blake                ┆ 18    │
│ Hrušková & Turek            ┆ 18    │
│ Hrubín & Trnka              ┆ 18    │
│ Potužníková & Jenčíková     ┆ 18    │
│ Voleská & Scheiner          ┆ 17    │
│ Schovancová & Schovanec     ┆ 17    │
│ Lebeda & Študlarová         ┆ 17    │
│ Brand & Wowk                ┆ 17    │
│ Štíplová & Vančurová        ┆ 17    │
│ Pospíšilová & Sušina        ┆ 17    │
│ Brandt & Lefin              ┆ 17    │
│ Ciprová & Němcová           ┆ 16    │
│ Beigel & Goff               ┆ 16    │
│ Johns & Barč                ┆ 16    │
│ Smolíková & Smolík          ┆ 16    │
│ Osborne & Knipping          ┆ 16    │
│ Rožnovská & Vydrová         ┆ 16    │
│ Simon & Ross                ┆ 16    │
│ Běhounek & Junek            ┆ 16    │
│ Grey & Ulč                  ┆ 15    │
│ …                           ┆ …     │
│ Martínek & Militký          ┆ 1     │
│ Seifert & Zeman             ┆ 1     │
│ Hrubý & Machata             ┆ 1     │
│ Pavlok & Jemelka            ┆ 1     │
│ Slach & Bouda               ┆ 1     │
│ Köhler & Sirotek            ┆ 1     │
│ Dvořák & Přenosilová        ┆ 1     │
│ Janouch & Kuriš             ┆ 1     │
│ McBrien & Marsh             ┆ 1     │
│ Vácha & Jiránek             ┆ 1     │
│ Novák & Vančura             ┆ 1     │
│ Gerber & Lee                ┆ 1     │
│ Hochmann & Zemina           ┆ 1     │
│ Zemina & Neubert            ┆ 1     │
│ Vinařický & Thuma           ┆ 1     │
│ Křelina & Hrach             ┆ 1     │
│ Hečko & Lukavský            ┆ 1     │
│ Jelen & Kračmar             ┆ 1     │
│ Narciso & Ferrari           ┆ 1     │
│ Stloukal & Marek            ┆ 1     │
│ Zdarsky & Bachalo           ┆ 1     │
│ Zapletal & Schmid           ┆ 1     │
│ Poe & Ketzek                ┆ 1     │
│ Zatloukalová & Kalinová     ┆ 1     │
│ Fleming & O'Donnell         ┆ 1     │
│ Navrátil & Zapletal         ┆ 1     │
│ Pacnerová & Crismer         ┆ 1     │
│ Thilo & Nöldner             ┆ 1     │
│ Šrut & Robejšková           ┆ 1     │
│ Aeschbacher & Bičovská      ┆ 1     │
│ Čarskaja & Urban            ┆ 1     │
│ Konigsburg & Šišková        ┆ 1     │
│ Prokeš & Šetelík            ┆ 1     │
│ Špinková & Kristová         ┆ 1     │
│ Brown & Koelsch             ┆ 1     │
│ Hamzatov & Mlčoch           ┆ 1     │
│ Kožík & Brun                ┆ 1     │
│ Kořínek & Klapač            ┆ 1     │
│ Karlíková & Fyman           ┆ 1     │
│ Fuka & Homolka              ┆ 1     │
│ Šimek & Bříza               ┆ 1     │
│ Kopta & Suchý               ┆ 1     │
│ Novák & Mysliveček          ┆ 1     │
│ Trelová & Sušina   

In [30]:
koliktohobylo = df_ill.unique(subset=['100_7','245_a']).filter(~pl.col("100_7").is_in(nechcemejetam)).filter(pl.col("stran") > 30).group_by(['dvojice']).agg(pl.col("245_a").n_unique()).sort(by="245_a",descending=True)

In [31]:
dvojice_aut_ill = df_ill.unique(subset=['100_7','245_a']).filter(~pl.col("100_7").is_in(nechcemejetam)).filter(pl.col("stran") > 30).group_by(['dvojice']).agg(pl.col("245_a").n_unique()).sort(by="245_a",descending=True).head(5).select(pl.col("dvojice")).to_series().to_list()
dvojice_aut_ill

['Štíplová & Němeček',
 'Švandrlík & Winter-Neprakta',
 'Pospíšilová & Trsťan',
 'Hašek & Lada',
 'Čapek & Čapek']

In [32]:
df_ill.filter(~pl.col("100_7").is_in(nechcemejetam)).group_by(['dvojice']).agg(pl.col("245_a").n_unique()).sort(by="245_a",descending=True)

shape: (32_296, 2)
┌────────────────────────────────┬───────┐
│ dvojice                        ┆ 245_a │
│ ---                            ┆ ---   │
│ str                            ┆ u32   │
╞════════════════════════════════╪═══════╡
│ Štíplová & Němeček             ┆ 108   │
│ Nedbalová & Popprová           ┆ 87    │
│ Nedbalová & Poppr              ┆ 68    │
│ Bass & Kratochvíl              ┆ 67    │
│ Švandrlík & Winter-Neprakta    ┆ 64    │
│ Čapek & Čapek                  ┆ 33    │
│ Pospíšilová & Trsťan           ┆ 31    │
│ Hašek & Lada                   ┆ 30    │
│ Rosecká & Růžička              ┆ 28    │
│ Škodová & Kubašta              ┆ 25    │
│ Pospíšilová & Vopičková        ┆ 25    │
│ Foglar & Čermák                ┆ 24    │
│ Čtvrtek & Pilař                ┆ 24    │
│ Piroddi & Baruzzi              ┆ 23    │
│ Tetourová & Plicková           ┆ 23    │
│ Macourek & Born                ┆ 22    │
│ Válková & Kopl                 ┆ 21    │
│ Drijverová & Otčenášek         ┆ 21    │
│ Bednářová & Šmarda             ┆ 21    │
│ Žáček & Born                   ┆ 21    │
│ Šavlíková & Roverová           ┆ 20    │
│ Steklač & Born                 ┆ 19    │
│ Pospíšilová & Vydrová          ┆ 19    │
│ Walliams & Ross                ┆ 19    │
│ Kratochvíl & Vydrová           ┆ 19    │
│ Grey & Hora                    ┆ 19    │
│ Webb & Williams                ┆ 19    │
│ Stará & Starý                  ┆ 19    │
│ Wenig & Wenig                  ┆ 18    │
│ Hrušková & Turek               ┆ 18    │
│ Dahl & Blake                   ┆ 18    │
│ Potužníková & Jenčíková        ┆ 18    │
│ Felix & Hísek                  ┆ 18    │
│ Hrubín & Trnka                 ┆ 18    │
│ Schovancová & Schovanec        ┆ 17    │
│ Pospíšilová & Sušina           ┆ 17    │
│ Brandt & Lefin                 ┆ 17    │
│ Brand & Wowk                   ┆ 17    │
│ Štíplová & Vančurová           ┆ 17    │
│ Voleská & Scheiner             ┆ 17    │
│ Lebeda & Študlarová            ┆ 17    │
│ Smolíková & Smolík             ┆ 16    │
│ Osborne & Knipping             ┆ 16    │
│ Beigel & Goff                  ┆ 16    │
│ Simon & Ross                   ┆ 16    │
│ Ciprová & Němcová              ┆ 16    │
│ Rožnovská & Vydrová            ┆ 16    │
│ Běhounek & Junek               ┆ 16    │
│ Johns & Barč                   ┆ 16    │
│ Eislerová & Šplíchal           ┆ 15    │
│ …                              ┆ …     │
│ Holková & Machourek            ┆ 1     │
│ Klimek & Martenek              ┆ 1     │
│ Freiwelligová & Vykypělová     ┆ 1     │
│ Kraifová & Hamarčák            ┆ 1     │
│ Pejchal & Pinc                 ┆ 1     │
│ Jiran & Zeman                  ┆ 1     │
│ Pikálek & Melan                ┆ 1     │
│ Chudožilov & Ogoun             ┆ 1     │
│ Bureš & Khunová                ┆ 1     │
│ Nohejl & Krásl                 ┆ 1     │
│ Adamovská & Sýkorová-Pekárková ┆ 1     │
│ Jiroušková & Boháčková         ┆ 1     │
│ Carey & Fabry                  ┆ 1     │
│ Rožek & Šimková                ┆ 1     │
│ Kleczek & Rosol                ┆ 1     │
│ Vapcarov & Hruška              ┆ 1     │
│ Coolen & Svolinský             ┆ 1     │
│ Formánková & Lacigová          ┆ 1     │
│ Wagner & O'Neill               ┆ 1     │
│ Adamus & Friedlová             ┆ 1     │
│ Baudyš & Štorkán               ┆ 1     │
│ Bednář & Paukert               ┆ 1     │
│ Bartíková & Šojdr              ┆ 1     │
│ Noha & Hoffmeister             ┆ 1     │
│ Wallace & Liszko               ┆ 1     │
│ Rázusová-Martáková & Dúbravec  ┆ 1     │
│ Slabý & Maňásek                ┆ 1     │
│ Houser & Filipe                ┆ 1     │
│ Lippold & Wernischová          ┆ 1     │
│ Šmidrkal & Macoun              ┆ 1     │
│ Koutná & Skřípková             ┆ 1     │
│ Namituche & Brožová            ┆ 1     │
│ Tyl & Muttich                  ┆ 1     │
│ Ježek & Vrbka                  ┆ 1     │
│ Chudožilov & Látal             ┆ 1     │
│ Šimonek & Wowk                 ┆ 1     │
│ Halas & Procházka      

In [33]:
import datetime

In [34]:
df_ill.filter(pl.col("dvojice") == "Pospíšilová & Trsťan")

shape: (37, 71)
┌──────────┬──────────────┬───────────────┬───────────┬───┬───────┬─────────────┬─────────────────┬───────────────┐
│ 100_ind1 ┆ 100_a        ┆ 100_7         ┆ 100_4     ┆ … ┆ stran ┆ jmeno1      ┆ jmeno2          ┆ dvojice       │
│ ---      ┆ ---          ┆ ---           ┆ ---       ┆   ┆ ---   ┆ ---         ┆ ---             ┆ ---           │
│ str      ┆ str          ┆ str           ┆ list[str] ┆   ┆ i64   ┆ str         ┆ str             ┆ str           │
╞══════════╪══════════════╪═══════════════╪═══════════╪═══╪═══════╪═════════════╪═════════════════╪═══════════════╡
│ 1        ┆ Pospíšilová, ┆ mzk2006331486 ┆ ["aut"]   ┆ … ┆ 72    ┆ Zuzana      ┆ Drahomír Trsťan ┆ Pospíšilová & │
│          ┆ Zuzana,      ┆               ┆           ┆   ┆       ┆ Pospíšilová ┆                 ┆ Trsťan        │
│ 1        ┆ Pospíšilová, ┆ mzk2006331486 ┆ ["aut"]   ┆ … ┆ 87    ┆ Zuzana      ┆ Drahomír Trsťan ┆ Pospíšilová & │
│          ┆ Zuzana,      ┆               ┆           ┆   ┆       ┆ Pospíšilová ┆                 ┆ Trsťan        │
│ 1        ┆ Pospíšilová, ┆ mzk2006331486 ┆ ["aut"]   ┆ … ┆ 72    ┆ Zuzana      ┆ Drahomír Trsťan ┆ Pospíšilová & │
│          ┆ Zuzana,      ┆               ┆           ┆   ┆       ┆ Pospíšilová ┆                 ┆ Trsťan        │
│ 1        ┆ Pospíšilová, ┆ mzk2006331486 ┆ ["aut"]   ┆ … ┆ 80    ┆ Zuzana      ┆ Drahomír Trsťan ┆ Pospíšilová & │
│          ┆ Zuzana,      ┆               ┆           ┆   ┆       ┆ Pospíšilová ┆                 ┆ Trsťan        │
│ 1        ┆ Pospíšilová, ┆ mzk2006331486 ┆ ["aut"]   ┆ … ┆ 70    ┆ Zuzana      ┆ Drahomír Trsťan ┆ Pospíšilová & │
│          ┆ Zuzana,      ┆               ┆           ┆   ┆       ┆ Pospíšilová ┆                 ┆ Trsťan        │
│ 1        ┆ Pospíšilová, ┆ mzk2006331486 ┆ ["aut"]   ┆ … ┆ 64    ┆ Zuzana      ┆ Drahomír Trsťan ┆ Pospíšilová & │
│          ┆ Zuzana,      ┆               ┆           ┆   ┆       ┆ Pospíšilová ┆                 ┆ Trsťan        │
│ 1        ┆ Pospíšilová, ┆ mzk2006331486 ┆ ["aut"]   ┆ … ┆ 104   ┆ Zuzana      ┆ Drahomír Trsťan ┆ Pospíšilová & │
│          ┆ Zuzana,      ┆               ┆           ┆   ┆       ┆ Pospíšilová ┆                 ┆ Trsťan        │
│ 1        ┆ Pospíšilová, ┆ mzk2006331486 ┆ ["aut"]   ┆ … ┆ 80    ┆ Zuzana      ┆ Drahomír Trsťan ┆ Pospíšilová & │
│          ┆ Zuzana,      ┆               ┆           ┆   ┆       ┆ Pospíšilová ┆                 ┆ Trsťan        │
│ 1        ┆ Pospíšilová, ┆ mzk2006331486 ┆ ["aut"]   ┆ … ┆ 116   ┆ Zuzana      ┆ Drahomír Trsťan ┆ Pospíšilová & │
│          ┆ Zuzana,      ┆               ┆           ┆   ┆       ┆ Pospíšilová ┆                 ┆ Trsťan        │
│ 1        ┆ Pospíšilová, ┆ mzk2006331486 ┆ ["aut"]   ┆ … ┆ 166   ┆ Zuzana      ┆ Drahomír Trsťan ┆ Pospíšilová & │
│          ┆ Zuzana,      ┆               ┆           ┆   ┆       ┆ Pospíšilová ┆                 ┆ Trsťan        │
│ 1        ┆ Pospíšilová, ┆ mzk2006331486 ┆ ["aut"]   ┆ … ┆ 71    ┆ Zuzana      ┆ Drahomír Trsťan ┆ Pospíšilová & │
│          ┆ Zuzana,      ┆               ┆           ┆   ┆       ┆ Pospíšilová ┆                 ┆ Trsťan        │
│ 1        ┆ Pospíšilová, ┆ mzk2006331486 ┆ ["aut"]   ┆ … ┆ 71    ┆ Zuzana      ┆ Drahomír Trsťan ┆ Pospíšilová & │
│          ┆ Zuzana,      ┆               ┆           ┆   ┆       ┆ Pospíšilová ┆                 ┆ Trsťan        │
│ 1        ┆ Pospíšilová, ┆ mzk2006331486 ┆ ["aut"]   ┆ … ┆ 71    ┆ Zuzana      ┆ Drahomír Trsťan ┆ Pospíšilová & │
│          ┆ Zuzana,      ┆               ┆           ┆   ┆       ┆ Pospíšilová ┆                 ┆ Trsťan        │
│ 1        ┆ Pospíšilová, ┆ mzk2006331486 ┆ ["aut"]   ┆ … ┆ 119   ┆ Zuzana      ┆ Drahomír Trsťan ┆ Pospíšilová & │
│          ┆ Zuzana,      ┆               ┆           ┆   ┆       ┆ Pospíšilová ┆                 ┆ Trsťan        │
│ 1        ┆ Pospíšilová, ┆ mzk2006331486 ┆ ["aut"]   ┆ … ┆ 72    ┆ Zuzana      ┆ Drahomír Trsťan ┆ Pospíšilová & │
│          ┆ Zuzana,      ┆             

In [35]:
do_grafu = df_ill.filter(
    pl.col("dvojice").is_in(dvojice_aut_ill)
).unique(
    subset=['245_a']
).join(
    koliktohobylo, how="left", on="dvojice"
).with_columns(
    pl.col("245_a_right").map_elements(lambda x: str(x) + "×")
).with_columns(
    pl.concat_str([pl.col('245_a_right'), pl.col('dvojice')], separator=' ').alias('dvojice')
)

In [36]:
dvojice_sort = do_grafu.group_by("dvojice").len().sort(by="len",descending=True).select(pl.col("dvojice")).to_series().to_list()
dvojice_sort

['104× Štíplová & Němeček',
 '63× Švandrlík & Winter-Neprakta',
 '27× Čapek & Čapek',
 '30× Pospíšilová & Trsťan',
 '28× Hašek & Lada']

In [37]:
df_ill.filter(pl.col("dvojice") == "Pospíšilová & Trsťan")

shape: (37, 71)
┌──────────┬──────────────┬───────────────┬───────────┬───┬───────┬─────────────┬─────────────────┬───────────────┐
│ 100_ind1 ┆ 100_a        ┆ 100_7         ┆ 100_4     ┆ … ┆ stran ┆ jmeno1      ┆ jmeno2          ┆ dvojice       │
│ ---      ┆ ---          ┆ ---           ┆ ---       ┆   ┆ ---   ┆ ---         ┆ ---             ┆ ---           │
│ str      ┆ str          ┆ str           ┆ list[str] ┆   ┆ i64   ┆ str         ┆ str             ┆ str           │
╞══════════╪══════════════╪═══════════════╪═══════════╪═══╪═══════╪═════════════╪═════════════════╪═══════════════╡
│ 1        ┆ Pospíšilová, ┆ mzk2006331486 ┆ ["aut"]   ┆ … ┆ 72    ┆ Zuzana      ┆ Drahomír Trsťan ┆ Pospíšilová & │
│          ┆ Zuzana,      ┆               ┆           ┆   ┆       ┆ Pospíšilová ┆                 ┆ Trsťan        │
│ 1        ┆ Pospíšilová, ┆ mzk2006331486 ┆ ["aut"]   ┆ … ┆ 87    ┆ Zuzana      ┆ Drahomír Trsťan ┆ Pospíšilová & │
│          ┆ Zuzana,      ┆               ┆           ┆   ┆       ┆ Pospíšilová ┆                 ┆ Trsťan        │
│ 1        ┆ Pospíšilová, ┆ mzk2006331486 ┆ ["aut"]   ┆ … ┆ 72    ┆ Zuzana      ┆ Drahomír Trsťan ┆ Pospíšilová & │
│          ┆ Zuzana,      ┆               ┆           ┆   ┆       ┆ Pospíšilová ┆                 ┆ Trsťan        │
│ 1        ┆ Pospíšilová, ┆ mzk2006331486 ┆ ["aut"]   ┆ … ┆ 80    ┆ Zuzana      ┆ Drahomír Trsťan ┆ Pospíšilová & │
│          ┆ Zuzana,      ┆               ┆           ┆   ┆       ┆ Pospíšilová ┆                 ┆ Trsťan        │
│ 1        ┆ Pospíšilová, ┆ mzk2006331486 ┆ ["aut"]   ┆ … ┆ 70    ┆ Zuzana      ┆ Drahomír Trsťan ┆ Pospíšilová & │
│          ┆ Zuzana,      ┆               ┆           ┆   ┆       ┆ Pospíšilová ┆                 ┆ Trsťan        │
│ 1        ┆ Pospíšilová, ┆ mzk2006331486 ┆ ["aut"]   ┆ … ┆ 64    ┆ Zuzana      ┆ Drahomír Trsťan ┆ Pospíšilová & │
│          ┆ Zuzana,      ┆               ┆           ┆   ┆       ┆ Pospíšilová ┆                 ┆ Trsťan        │
│ 1        ┆ Pospíšilová, ┆ mzk2006331486 ┆ ["aut"]   ┆ … ┆ 104   ┆ Zuzana      ┆ Drahomír Trsťan ┆ Pospíšilová & │
│          ┆ Zuzana,      ┆               ┆           ┆   ┆       ┆ Pospíšilová ┆                 ┆ Trsťan        │
│ 1        ┆ Pospíšilová, ┆ mzk2006331486 ┆ ["aut"]   ┆ … ┆ 80    ┆ Zuzana      ┆ Drahomír Trsťan ┆ Pospíšilová & │
│          ┆ Zuzana,      ┆               ┆           ┆   ┆       ┆ Pospíšilová ┆                 ┆ Trsťan        │
│ 1        ┆ Pospíšilová, ┆ mzk2006331486 ┆ ["aut"]   ┆ … ┆ 116   ┆ Zuzana      ┆ Drahomír Trsťan ┆ Pospíšilová & │
│          ┆ Zuzana,      ┆               ┆           ┆   ┆       ┆ Pospíšilová ┆                 ┆ Trsťan        │
│ 1        ┆ Pospíšilová, ┆ mzk2006331486 ┆ ["aut"]   ┆ … ┆ 166   ┆ Zuzana      ┆ Drahomír Trsťan ┆ Pospíšilová & │
│          ┆ Zuzana,      ┆               ┆           ┆   ┆       ┆ Pospíšilová ┆                 ┆ Trsťan        │
│ 1        ┆ Pospíšilová, ┆ mzk2006331486 ┆ ["aut"]   ┆ … ┆ 71    ┆ Zuzana      ┆ Drahomír Trsťan ┆ Pospíšilová & │
│          ┆ Zuzana,      ┆               ┆           ┆   ┆       ┆ Pospíšilová ┆                 ┆ Trsťan        │
│ 1        ┆ Pospíšilová, ┆ mzk2006331486 ┆ ["aut"]   ┆ … ┆ 71    ┆ Zuzana      ┆ Drahomír Trsťan ┆ Pospíšilová & │
│          ┆ Zuzana,      ┆               ┆           ┆   ┆       ┆ Pospíšilová ┆                 ┆ Trsťan        │
│ 1        ┆ Pospíšilová, ┆ mzk2006331486 ┆ ["aut"]   ┆ … ┆ 71    ┆ Zuzana      ┆ Drahomír Trsťan ┆ Pospíšilová & │
│          ┆ Zuzana,      ┆               ┆           ┆   ┆       ┆ Pospíšilová ┆                 ┆ Trsťan        │
│ 1        ┆ Pospíšilová, ┆ mzk2006331486 ┆ ["aut"]   ┆ … ┆ 119   ┆ Zuzana      ┆ Drahomír Trsťan ┆ Pospíšilová & │
│          ┆ Zuzana,      ┆               ┆           ┆   ┆       ┆ Pospíšilová ┆                 ┆ Trsťan        │
│ 1        ┆ Pospíšilová, ┆ mzk2006331486 ┆ ["aut"]   ┆ … ┆ 72    ┆ Zuzana      ┆ Drahomír Trsťan ┆ Pospíšilová & │
│          ┆ Zuzana,      ┆             

In [38]:
dvojice_sort

['104× Štíplová & Němeček',
 '63× Švandrlík & Winter-Neprakta',
 '27× Čapek & Čapek',
 '30× Pospíšilová & Trsťan',
 '28× Hašek & Lada']

In [136]:
base_ill = alt.Chart(
    alt_friendly(do_grafu), 
    title=alt.TitleParams(f"{len(dvojice_aut_ill)} nejčastějších dvojic psali-ilustrovali (bez reprintů)")).mark_circle() 

tecky_ill = base_ill.encode(
            x=alt.X("rok:T", title=None, axis=alt.Axis(domainOpacity=0, tickColor='#DCDDD6')), 
            y=alt.Y("dvojice:N", sort=dvojice_sort, title=None, axis=alt.Axis(orient='left', domainOpacity=0, tickColor='white', labelExpr='split(datum.label, "× ")[1]')), 
            yOffset=alt.YOffset("jitter:Q", scale=alt.Scale(range=[3, 15])), 
            color=alt.Color('dvojice:N', scale=alt.Scale(range=['#E09DA3']), 
                            sort=dvojice_sort).legend(None)) \
        .transform_calculate(jitter="sqrt(-2*log(random()))*cos(2*PI*random())")

pocty_ill = base_ill.mark_text().encode(x=alt.X('rok:T', title=None), 
    y=alt.Y('dvojice:N', title=None, sort=dvojice_sort, axis=alt.Axis(orient="right", tickColor='white', labelExpr='split(datum.label, " ")[0]')))

zebricek_ill = alt.layer(tecky_ill, pocty_ill).configure_view(stroke='transparent').properties(
    width=kredity['sirka'], 
    autosize={'type': 'fit', 'contains': 'padding'}
)

zebricek_ill

alt.LayerChart(...)

In [40]:
do_grafu.filter(pl.col('100_a').str.contains('Hašek')).select(pl.col("245_a")).to_series().to_list()

['Osudy dobrého vojáka Švejka za světové války',
 'Nešťastný policejní ředitel',
 'Malá zoologická zahrada',
 'Veselé povídky',
 'Aféra s křečkem a jiné povídky',
 'Procházka přes hranice',
 'Dekameron humoru a satiry',
 'Všivá historie a jiné humoresky',
 'Turista Aratáš a jiné humoresky',
 'Humoresky',
 'Reelní podnik',
 'Když kvetou třešně a jiné humoresky',
 'Švejk před světovou válkou, Velitelem města Bugulmy a další příběhy',
 'Potměšilé historie',
 'Za války i za sovětů v Rusku',
 'Osudy dobrého vojáka Švejka',
 'Útrapy vychovatele',
 'Oslí historie, aneb, Vojenské články do čítanek',
 'Dobrý voják Švejk před válkou a jiné podivné historky',
 'Ze staré droguerie',
 'Průvodčí cizinců a jiné satiry z cest i z domova',
 'Smějeme se s Jaroslavem Haškem',
 'Zpověď starého mládence',
 'Postrach domu',
 'Když bolševici zrušili Vánoce',
 'Má drahá přítelkyně Julča',
 'Dva tucty povídek',
 'Hašek v kostce',
 'Povídky',
 'Pod věchýtkem humoru']

In [138]:
me_to_neurazi(zebricek_ill, soubor="02_psali_ilustrovali", kredity=kredity['default'])

<figure>
    <a href="https://data.irozhlas.cz/knihy-grafy/02_psali_ilustrovali.svg" target="_blank">
    <img src="https://data.irozhlas.cz/knihy-grafy/02_psali_ilustrovali.svg" width="100%" alt="Omlouváme se, ale alternativní text se nepodařilo vygenerovat. Texty v grafu by měly být čitelné ze zdrojového souboru SVG." />
    </a>
    </figure>


In [42]:
df_ill.group_by(['100_a','100_7','700_a']).agg(pl.col("245_a").n_unique()).sort(by="245_a",descending=True)

shape: (34_493, 4)
┌─────────────────────────────────┬───────────────────┬────────────────────────────┬───────┐
│ 100_a                           ┆ 100_7             ┆ 700_a                      ┆ 245_a │
│ ---                             ┆ ---               ┆ ---                        ┆ ---   │
│ str                             ┆ str               ┆ str                        ┆ u32   │
╞═════════════════════════════════╪═══════════════════╪════════════════════════════╪═══════╡
│ Štíplová, Ljuba,                ┆ jk01131441        ┆ Němeček, Jaroslav,         ┆ 108   │
│ Nedbalová, Marie                ┆ jo2014816080      ┆ Popprová, Andrea           ┆ 87    │
│ Nedbalová, Marie                ┆ jo2014816080      ┆ Poppr, Roman               ┆ 68    │
│ Bass, Eduard,                   ┆ jk01011066        ┆ Kratochvíl, Zdeněk,        ┆ 67    │
│ Švandrlík, Miloslav,            ┆ jk01131832        ┆ Winter-Neprakta, Jiří,     ┆ 64    │
│ Wilson, Jacqueline,             ┆ jn20010310318     ┆ Sharratt, Nick,            ┆ 52    │
│ Delahaye, Gilbert,              ┆ xx0203193         ┆ Marlier, Marcel,           ┆ 51    │
│ Verne, Jules,                   ┆ jn19990008769     ┆ Benett, Léon,              ┆ 50    │
│ Brezina, Thomas,                ┆ jn20001227589     ┆ Fearn, Naomi,              ┆ 43    │
│ Verne, Jules,                   ┆ jn19990008769     ┆ Roux, George,              ┆ 42    │
│ Goscinny, René,                 ┆ jn20000602144     ┆ Uderzo, Albert,            ┆ 42    │
│ Deary, Terry,                   ┆ jn20001103401     ┆ Brown, Martin,             ┆ 36    │
│ Arnold, Nick,                   ┆ xx0008006         ┆ De Saulles, Tony           ┆ 33    │
│ Čapek, Karel,                   ┆ jk01021023        ┆ Čapek, Josef,              ┆ 33    │
│ Pospíšilová, Zuzana,            ┆ mzk2006331486     ┆ Trsťan, Drahomír,          ┆ 31    │
│ Hašek, Jaroslav,                ┆ jk01040097        ┆ Lada, Josef,               ┆ 29    │
│ Meadows, Daisy                  ┆ xx0082647         ┆ Ripper, Georgie,           ┆ 29    │
│ Rosecká, Zdena                  ┆ jx20031130107     ┆ Růžička, Jiří              ┆ 28    │
│ Škodová, Helena,                ┆ jx20040618039     ┆ Kubašta, Vojtěch,          ┆ 25    │
│ Pospíšilová, Zuzana,            ┆ mzk2006331486     ┆ Vopičková, Vladimíra       ┆ 25    │
│ Čtvrtek, Václav,                ┆ jk01021929        ┆ Pilař, Radek,              ┆ 24    │
│ Awdry, W.,                      ┆ xx0010566         ┆ Davies, Robin,             ┆ 24    │
│ Awdry, W.,                      ┆ xx0010566         ┆ Smith, Jerry               ┆ 23    │
│ Burroughs, Edgar Rice,          ┆ jn19990001239     ┆ Pešek, Richard,            ┆ 23    │
│ Tetourová, Marie,               ┆ jn20001005512     ┆ Plicková, Edita,           ┆ 23    │
│ Piroddi, Chiara,                ┆ osa2017965599     ┆ Baruzzi, Agnese,           ┆ 23    │
│ Macourek, Miloš,                ┆ jk01072813        ┆ Born, Adolf,               ┆ 22    │
│ Foglar, Jaroslav,               ┆ jk01031485        ┆ Čermák, Marko,             ┆ 22    │
│ Žáček, Jiří,                    ┆ jk01152946        ┆ Born, Adolf,               ┆ 21    │
│ May, Karl,                      ┆ jn19990005499     ┆ Krum, Gustav,              ┆ 21    │
│ Válková, Veronika,              ┆ jo2005274171      ┆ Kopl, Petr,                ┆ 21    │
│ Drijverová, Martina,            ┆ jk01023067        ┆ Otčenášek, Vojtěch,        ┆ 21    │
│ Bednářová, Jiřina,              ┆ mzk2004248919     ┆ Šmarda, Richard,           ┆ 21    │
│ Šavlíková, Lucie,               ┆ jn19981002458     ┆ Roverová, Eva              ┆ 20    │
│ Kratochvíl, Miloš,              ┆ jk01062996        ┆ Vydrová, Markéta,          ┆ 19    │
│ Walliams, David,                ┆ xx0158956         ┆ Ross, Tony,                ┆ 19    │
│ Stará, Ester,                   ┆ mzk2004261153     ┆ Starý, Milan,              ┆ 19    │
│ Webb, Holly                     ┆ ola2010577122     ┆ Williams, Sophy    

In [43]:
ctyrlistek_leader = " <leader>     cam a22      a 4500"
ctyrlistek_leader = ctyrlistek_leader.split(">")[1]
print(ctyrlistek_leader[6])
print(ctyrlistek_leader[7])

a
m


In [44]:
df.filter(pl.col('700_4') == 'ill').filter(~pl.col("100_7").is_in(nechcemejetam)).group_by(['100_a','100_7','700_a']).agg(pl.col("245_a").n_unique()).sort(by="245_a",descending=True).rename({'100_a':'autor/ka','700_a':'ilustrátor/ka','245_a':'společných knih'}).drop("100_7")

shape: (32_606, 3)
┌───────────────────────────────┬─────────────────────────────┬─────────────────┐
│ autor/ka                      ┆ ilustrátor/ka               ┆ společných knih │
│ ---                           ┆ ---                         ┆ ---             │
│ str                           ┆ str                         ┆ u32             │
╞═══════════════════════════════╪═════════════════════════════╪═════════════════╡
│ Štíplová, Ljuba,              ┆ Němeček, Jaroslav,          ┆ 108             │
│ Nedbalová, Marie              ┆ Popprová, Andrea            ┆ 87              │
│ Nedbalová, Marie              ┆ Poppr, Roman                ┆ 68              │
│ Bass, Eduard,                 ┆ Kratochvíl, Zdeněk,         ┆ 67              │
│ Švandrlík, Miloslav,          ┆ Winter-Neprakta, Jiří,      ┆ 64              │
│ Čapek, Karel,                 ┆ Čapek, Josef,               ┆ 33              │
│ Pospíšilová, Zuzana,          ┆ Trsťan, Drahomír,           ┆ 31              │
│ Hašek, Jaroslav,              ┆ Lada, Josef,                ┆ 29              │
│ Rosecká, Zdena                ┆ Růžička, Jiří               ┆ 28              │
│ Pospíšilová, Zuzana,          ┆ Vopičková, Vladimíra        ┆ 25              │
│ Škodová, Helena,              ┆ Kubašta, Vojtěch,           ┆ 25              │
│ Čtvrtek, Václav,              ┆ Pilař, Radek,               ┆ 24              │
│ Tetourová, Marie,             ┆ Plicková, Edita,            ┆ 23              │
│ Piroddi, Chiara,              ┆ Baruzzi, Agnese,            ┆ 23              │
│ Macourek, Miloš,              ┆ Born, Adolf,                ┆ 22              │
│ Foglar, Jaroslav,             ┆ Čermák, Marko,              ┆ 22              │
│ Bednářová, Jiřina,            ┆ Šmarda, Richard,            ┆ 21              │
│ Žáček, Jiří,                  ┆ Born, Adolf,                ┆ 21              │
│ Drijverová, Martina,          ┆ Otčenášek, Vojtěch,         ┆ 21              │
│ Válková, Veronika,            ┆ Kopl, Petr,                 ┆ 21              │
│ Šavlíková, Lucie,             ┆ Roverová, Eva               ┆ 20              │
│ Stará, Ester,                 ┆ Starý, Milan,               ┆ 19              │
│ Webb, Holly                   ┆ Williams, Sophy             ┆ 19              │
│ Walliams, David,              ┆ Ross, Tony,                 ┆ 19              │
│ Pospíšilová, Zuzana,          ┆ Vydrová, Markéta,           ┆ 19              │
│ Grey, Zane,                   ┆ Hora, Jan,                  ┆ 19              │
│ Steklač, Vojtěch,             ┆ Born, Adolf,                ┆ 19              │
│ Kratochvíl, Miloš,            ┆ Vydrová, Markéta,           ┆ 19              │
│ Dahl, Roald,                  ┆ Blake, Quentin,             ┆ 18              │
│ Potužníková, Ema              ┆ Jenčíková, Lucie            ┆ 18              │
│ Felix, Jiří,                  ┆ Hísek, Květoslav,           ┆ 18              │
│ Hrušková, Marie,              ┆ Turek, Jaroslav,            ┆ 18              │
│ Hrubín, František,            ┆ Trnka, Jiří,                ┆ 18              │
│ Brand, Max,                   ┆ Wowk, Jiří,                 ┆ 17              │
│ Štíplová, Ljuba,              ┆ Janoušková Vančurová, Alena ┆ 17              │
│ Schovancová, Běla,            ┆ Schovanec, Ladislav,        ┆ 17              │
│ Pospíšilová, Zuzana,          ┆ Sušina, Michal              ┆ 17              │
│ Voleská, Marta,               ┆ Scheiner, Artuš,            ┆ 17              │
│ Lebeda, Jan,                  ┆ Študlarová, Zdeňka,         ┆ 17              │
│ Brandt, Susanne,              ┆ Lefin, Petra,               ┆ 17              │
│ Beigel, Christine,            ┆ Le Goff, Hervé,             ┆ 16              │
│ Ciprová, Oldřiška,            ┆ Němcová, Lenka,             ┆ 16              │
│ Osborne, Mary Pope,           ┆ Knipping, Jutta,            ┆ 16              │
│ Johns, William Earl,          ┆ Barč, Petr,

In [45]:
df.filter(pl.col('700_4') == 'trl').group_by(['100_a','100_7','700_a']).agg(pl.col("245_a").n_unique()).sort(by="245_a",descending=True)

shape: (66_400, 4)
┌─────────────────────────────────┬───────────────────┬───────────────────────────┬───────┐
│ 100_a                           ┆ 100_7             ┆ 700_a                     ┆ 245_a │
│ ---                             ┆ ---               ┆ ---                       ┆ ---   │
│ str                             ┆ str               ┆ str                       ┆ u32   │
╞═════════════════════════════════╪═══════════════════╪═══════════════════════════╪═══════╡
│ Unger, Gert F.,                 ┆ jn20001103529     ┆ Butala, Tomáš,            ┆ 311   │
│ Kirby, John                     ┆ jx20040611003     ┆ Pavka, Marek,             ┆ 182   │
│ Courths-Mahler, Hedwig,         ┆ jn19990001513     ┆ Schönová, Zuzana          ┆ 120   │
│ Scott, William,                 ┆ ola2003188680     ┆ Butala, Tomáš,            ┆ 101   │
│ Unger, Gert F.,                 ┆ jn20001103529     ┆ Schönová, Zuzana          ┆ 80    │
│ Birkner-Mahler, Frieda,         ┆ jn20000600873     ┆ Lacinová, Libuše,         ┆ 80    │
│ Unger, Gert F.,                 ┆ jn20001103529     ┆ Sedláčková, Libuše        ┆ 77    │
│ Pratchett, Terry,               ┆ jo20000080627     ┆ Kantůrek, Jan,            ┆ 57    │
│ Brezina, Thomas,                ┆ jn20001227589     ┆ Steidlová, Dagmar,        ┆ 55    │
│ Courths-Mahler, Hedwig,         ┆ jn19990001513     ┆ Lacinová, Libuše,         ┆ 54    │
│ Lane, Lex                       ┆ ola2007364818     ┆ Pavka, Marek,             ┆ 53    │
│ Dark, Jason,                    ┆ jn20000810032     ┆ Sychra, Pavel             ┆ 50    │
│ Nieritz, Gustav,                ┆ jo20000080760     ┆ Tomsa, František Bohumil, ┆ 49    │
│ Unger, Gert F.,                 ┆ jn20001103529     ┆ Sychra, Pavel             ┆ 48    │
│ Dark, Jason,                    ┆ jn20000810032     ┆ Küchler, Marek            ┆ 48    │
│ Hayes, Rex,                     ┆ jn20020717154     ┆ Pavka, Marek,             ┆ 47    │
│ Shakespeare, William,           ┆ jn19981002129     ┆ Sládek, Josef Václav,     ┆ 46    │
│ Etzold, Hans-Rüdiger,           ┆ xx0020263         ┆ Hlásek, Pavel             ┆ 45    │
│ Steiner, Rudolf,                ┆ jn19990009728     ┆ Hradil, Radomil,          ┆ 45    │
│ Wallace, Edgar,                 ┆ jn19990008883     ┆ Heller, František         ┆ 43    │
│ Francis, Dick,                  ┆ jn19990002376     ┆ Moserová, Jaroslava,      ┆ 43    │
│ Davis, Jim,                     ┆ jn20010601536     ┆ Škába, Filip,             ┆ 42    │
│ Shakespeare, William,           ┆ jn19981002129     ┆ Hilský, Martin,           ┆ 42    │
│ Mark, William,                  ┆ jo20241218643     ┆ Kuťák, Jaroslav,          ┆ 42    │
│ Velden, Irene von               ┆ jx20031204026     ┆ Chromiaková, Eva          ┆ 40    │
│ May, Karl,                      ┆ jn19990005499     ┆ Šunda, Vladimír           ┆ 39    │
│ Unger, Gert F.,                 ┆ jn20001103529     ┆ Veselý, Milan             ┆ 38    │
│ Wilson, Jacqueline,             ┆ jn20010310318     ┆ Feltová, Daniela,         ┆ 38    │
│ Verne, Jules,                   ┆ jn19990008769     ┆ Unzeitig, Vítězslav,      ┆ 38    │
│ Patterson, James,               ┆ jo20000076489     ┆ Duha, Ondřej              ┆ 35    │
│ Wild, Dunja                     ┆ ola20040510003    ┆ Smolaková, Helena         ┆ 35    │
│ Dark, Jason,                    ┆ jn20000810032     ┆ Brzobohatý, Rostislav     ┆ 35    │
│ Andrée, Michaela                ┆ ola2003188685     ┆ Smolaková, Helena         ┆ 34    │
│ Cartland, Barbara,              ┆ jn19990001350     ┆ Volná, Kristina,          ┆ 34    │
│ Platón,                         ┆ jn19981001996     ┆ Novotný, František,       ┆ 33    │
│ McBain, Ed,                     ┆ jn19981001834     ┆ Maxová, Alena,            ┆ 33    │
│ Ošó,                            ┆ jn19981001926     ┆ Žlábková, Jana,           ┆ 32    │
│ King, Stephen,                  ┆ jn19990004346     ┆ Bartošková, Linda,        ┆ 32    │
│ Everett, Jack,         

In [46]:
df.filter(pl.col('700_4') == 'ill').group_by('700_a').agg(pl.col("100_a").n_unique()).sort(by="100_a",descending=True)

shape: (13_657, 2)
┌──────────────────────────┬───────┐
│ 700_a                    ┆ 100_a │
│ ---                      ┆ ---   │
│ str                      ┆ u32   │
╞══════════════════════════╪═══════╡
│ Born, Adolf,             ┆ 149   │
│ Bouda, Cyril,            ┆ 114   │
│ Burian, Zdeněk,          ┆ 112   │
│ Krejčová, Zdeňka,        ┆ 98    │
│ Svolinský, Karel,        ┆ 93    │
│ Zmatlíková, Helena,      ┆ 80    │
│ Aleš, Mikoláš,           ┆ 80    │
│ Petráček, Jiří,          ┆ 78    │
│ Jiránek, Vladimír,       ┆ 75    │
│ Šplíchal, Antonín,       ┆ 73    │
│ Slíva, Jiří,             ┆ 73    │
│ Černý, Věnceslav,        ┆ 69    │
│ Thuma, Karel Ladislav,   ┆ 67    │
│ Čuma, Aleš,              ┆ 67    │
│ Plicková, Edita,         ┆ 67    │
│ Procházka, Otakar        ┆ 65    │
│ Winter-Neprakta, Jiří,   ┆ 65    │
│ Teissig, Karel,          ┆ 65    │
│ Komárek, Vladimír,       ┆ 61    │
│ Lhoták, Kamil,           ┆ 61    │
│ Lada, Josef,             ┆ 61    │
│ Janeček, Ota,            ┆ 60    │
│ Urban, Petr,             ┆ 60    │
│ Martenek, Miloslav,      ┆ 58    │
│ Fixl, Jiří,              ┆ 55    │
│ Kabát, Václav,           ┆ 55    │
│ Černý, Jan,              ┆ 55    │
│ Netopil, Zdeněk,         ┆ 53    │
│ Velčovský, Josef,        ┆ 53    │
│ Tesař, Vladimír,         ┆ 53    │
│ Jakešová, Miroslava,     ┆ 52    │
│ Čutta, Václav,           ┆ 52    │
│ Škoda, František,        ┆ 51    │
│ Duda, Stanislav,         ┆ 50    │
│ Trnka, Jiří,             ┆ 49    │
│ Renčín, Vladimír,        ┆ 49    │
│ Kalousek, Jiří,          ┆ 48    │
│ Čechová, Olga,           ┆ 48    │
│ Váša, Miroslav,          ┆ 46    │
│ Konůpek, Jan,            ┆ 45    │
│ Scheiner, Artuš,         ┆ 45    │
│ Nesvadba, Miloš,         ┆ 44    │
│ Zpěvák, Karel            ┆ 44    │
│ Kovařík, Jindřich,       ┆ 44    │
│ Barták, Miroslav,        ┆ 44    │
│ Jágr, Miloslav,          ┆ 43    │
│ Drobný, Libor,           ┆ 42    │
│ Anlauf, Lubomír,         ┆ 42    │
│ Franta, Karel,           ┆ 42    │
│ Mézl, Zdeněk,            ┆ 41    │
│ …                        ┆ …     │
│ Bergerová, Jana,         ┆ 1     │
│ Hron, Petr,              ┆ 1     │
│ Hromková, Blanka         ┆ 1     │
│ Bubeníček, Jindřich,     ┆ 1     │
│ Sikora, František        ┆ 1     │
│ Zvelebil, Kamil,         ┆ 1     │
│ Plekanec, Miroslav,      ┆ 1     │
│ Calero, Dennis,          ┆ 1     │
│ Baumgartlová, Jana,      ┆ 1     │
│ Ruggiero, Lorenzo,       ┆ 1     │
│ Collin, Hedvig,          ┆ 1     │
│ Klímová, Petra           ┆ 1     │
│ Janovská, Marika         ┆ 1     │
│ Maleček, Roman           ┆ 1     │
│ Pincová, Vanda           ┆ 1     │
│ Planck, Willy,           ┆ 1     │
│ Flanigan, Ruth J.        ┆ 1     │
│ Lawson, Nan              ┆ 1     │
│ Slivka, Dušan,           ┆ 1     │
│ Černohorská, Olga        ┆ 1     │
│ Švaňhalová, Vendula,     ┆ 1     │
│ Fei, Shen                ┆ 1     │
│ Dmytrenko, V. H.         ┆ 1     │
│ Stambecco,               ┆ 1     │
│ Zinnerová, Markéta,      ┆ 1     │
│ Lepšík, Jan,             ┆ 1     │
│ Freitag, Wolfgang,       ┆ 1     │
│ Orpinas, Jean-Paul       ┆ 1     │
│ Bouda, Boris             ┆ 1     │
│ Bahas                    ┆ 1     │
│ Žižka, Josef             ┆ 1     │
│ Sullivan, Lee,           ┆ 1     │
│ Kristiansen, Ingvild Th. ┆ 1     │
│ Chytilová, Dobruše       ┆ 1     │
│ Krch, Martin,            ┆ 1     │
│ Antoš, Ivan              ┆ 1     │
│ Česák, Jiří,             ┆ 1     │
│ Winter, Quinton          ┆ 1     │
│ Sobotka, František,      ┆ 1     │
│ Gavlas, Antonín,         ┆ 1     │
│ Appen, Karl von,         ┆ 1     │
│ Tulip, Jenny             ┆ 1     │
│ Cassirer, Philip,        ┆ 1     │
│ Komárek, Stanislav,      ┆ 1     │
│ Gay, Barbara             ┆ 1     │
│ Antalovský, Jiří         ┆ 1     │
│ Tangen, Dieter           ┆ 1     │
│ Salomó, Xavier,          ┆ 1     │
│ Bárta, Marcel,           ┆ 1     │
│ Novák, Viktor            ┆ 1     │
└──────────────────────────┴───────┘

In [47]:
nejaktivnejsi_ilustratori = df.filter(pl.col("stran") > 30).filter(pl.col('700_4') == 'ill').group_by('700_7').agg(pl.struct(["100_a","245_a"]).n_unique()).sort(by="100_a",descending=True).head(11).select(pl.col("700_7")).to_series().to_list()
nejaktivnejsi_ilustratori = [x for x in nejaktivnejsi_ilustratori if x != None]
nejaktivnejsi_ilustratori

['jk01012660',
 'jk01020396',
 'jk01083186',
 'jk01083128',
 'jk01012795',
 'jk01063265',
 'jk01152754',
 'jk01021645',
 'jk01132366',
 'ola2003162788']

In [48]:
def hezkejmeno(sto):
    if not sto[-1].isalnum():
        sto = sto[:-1]
    if "," in sto:
        sto = sto.split(",")
        sto = sto[1].strip() + " " + sto[0].strip()
    return sto    

In [49]:
do_grafu2 = df.filter(pl.col('700_7').is_in(nejaktivnejsi_ilustratori)).with_columns(pl.col('700_a').map_elements(hezkejmeno)).with_columns(pl.col("rok").map_elements(lambda x: datetime.date(year=int(x), month=1, day=1), return_dtype=pl.Date).cast(pl.Datetime))
nejaktivnejsi_ilustratori2 = do_grafu2.group_by('700_a').agg(pl.struct(["100_a","245_a"]).n_unique()).sort(by="100_a",descending=True).head(10).select(pl.col("700_a")).to_series().to_list()
mrtvi_ilustratori = aut.explode("100_7").filter(pl.col('100_7').is_in(nejaktivnejsi_ilustratori)).explode("046_g").with_columns(pl.col("046_g").map_elements(lambda x: int(x)).alias("umrti")).select(pl.col(["100_7","umrti"])).filter(pl.col('umrti').is_between(1800,2025)).with_columns(pl.col("umrti").map_elements(lambda x: datetime.date(year=int(x), month=1, day=1), return_dtype=pl.Date).cast(pl.Datetime))
do_grafu2 = do_grafu2.join(mrtvi_ilustratori, how='left', left_on='700_7', right_on='100_7').join(
    do_grafu2.group_by('700_7').len(), on='700_7', how='left'
).with_columns(
    pl.col("len").map_elements(lambda x: str(x) + "×")
).with_columns(
    pl.concat_str([pl.col('len'), pl.col('700_a')], separator=' ').alias('700_a')
)
nejaktivnejsi_ilustratori2 = do_grafu2.group_by('700_a').len().sort(by='len',descending=True).select(pl.col('700_a')).to_series().to_list()

In [50]:
mrtvi_ilustratori

shape: (7, 2)
┌────────────┬─────────────────────┐
│ 100_7      ┆ umrti               │
│ ---        ┆ ---                 │
│ str        ┆ datetime[μs]        │
╞════════════╪═════════════════════╡
│ jk01012660 ┆ 2016-01-01 00:00:00 │
│ jk01012795 ┆ 1984-01-01 00:00:00 │
│ jk01020396 ┆ 1981-01-01 00:00:00 │
│ jk01021645 ┆ 1936-01-01 00:00:00 │
│ jk01132366 ┆ 1917-01-01 00:00:00 │
│ jk01083186 ┆ 2011-01-01 00:00:00 │
│ jk01152754 ┆ 2005-01-01 00:00:00 │
└────────────┴─────────────────────┘

In [51]:
nejaktivnejsi_ilustratori2

['457× Zdeněk Burian',
 '451× Helena Zmatlíková',
 '445× Adolf Born',
 '254× Antonín Šplíchal',
 '252× Cyril Bouda',
 '233× Jiří Winter-Neprakta',
 '204× Věnceslav Černý',
 '198× Zdeňka Krejčová',
 '197× Jaroslav Němeček',
 '169× Karel Ladislav Thuma']

In [52]:
do_grafu2.sample(5)

shape: (5, 70)
┌──────────┬──────────────────────┬───────────────┬───────────┬───┬──────────────┬───────┬──────────────────────┬──────┐
│ 100_ind1 ┆ 100_a                ┆ 100_7         ┆ 100_4     ┆ … ┆ rok          ┆ stran ┆ umrti                ┆ len  │
│ ---      ┆ ---                  ┆ ---           ┆ ---       ┆   ┆ ---          ┆ ---   ┆ ---                  ┆ ---  │
│ str      ┆ str                  ┆ str           ┆ list[str] ┆   ┆ datetime[μs] ┆ i64   ┆ datetime[μs]         ┆ str  │
╞══════════╪══════════════════════╪═══════════════╪═══════════╪═══╪══════════════╪═══════╪══════════════════════╪══════╡
│ 1        ┆ Hrnčíř, Svatopluk,   ┆ jk01042788    ┆ ["aut"]   ┆ … ┆ 1995-01-01   ┆ 75    ┆ 2016-01-01 00:00:00  ┆ 445× │
│          ┆                      ┆               ┆           ┆   ┆ 00:00:00     ┆       ┆                      ┆      │
│ 1        ┆ Neruda, Jan,         ┆ jk01083209    ┆ ["aut"]   ┆ … ┆ 1954-01-01   ┆ 104   ┆ 1984-01-01 00:00:00  ┆ 252× │
│          ┆                      ┆               ┆           ┆   ┆ 00:00:00     ┆       ┆                      ┆      │
│ 1        ┆ Bielicki, Marian     ┆ jn19981000263 ┆ ["aut"]   ┆ … ┆ 1964-01-01   ┆ 145   ┆ 2016-01-01 00:00:00  ┆ 445× │
│          ┆ Leon,                ┆               ┆           ┆   ┆ 00:00:00     ┆       ┆                      ┆      │
│ 1        ┆ Vlasáková, Julie,    ┆ jk01150061    ┆ ["aut"]   ┆ … ┆ 1944-01-01   ┆ 124   ┆ 1936-01-01 00:00:00  ┆ 204× │
│          ┆                      ┆               ┆           ┆   ┆ 00:00:00     ┆       ┆                      ┆      │
│ 1        ┆ Nečas, Jan           ┆ jk01082827    ┆ ["aut"]   ┆ … ┆ 1895-01-01   ┆ 42    ┆ 1917-01-01 00:00:00  ┆ 169× │
│          ┆ Evangelista,         ┆               ┆           ┆   ┆ 00:00:00     ┆       ┆                      ┆      │
└──────────┴──────────────────────┴───────────────┴───────────┴───┴──────────────┴───────┴──────────────────────┴──────┘

In [53]:
nejaktivnejsi_ilustratori2

['457× Zdeněk Burian',
 '451× Helena Zmatlíková',
 '445× Adolf Born',
 '254× Antonín Šplíchal',
 '252× Cyril Bouda',
 '233× Jiří Winter-Neprakta',
 '204× Věnceslav Černý',
 '198× Zdeňka Krejčová',
 '197× Jaroslav Němeček',
 '169× Karel Ladislav Thuma']

In [54]:
do_grafu2.sample(3)

shape: (3, 70)
┌──────────┬───────────────────┬───────────────┬───────────┬───┬──────────────┬───────┬─────────────────────┬──────┐
│ 100_ind1 ┆ 100_a             ┆ 100_7         ┆ 100_4     ┆ … ┆ rok          ┆ stran ┆ umrti               ┆ len  │
│ ---      ┆ ---               ┆ ---           ┆ ---       ┆   ┆ ---          ┆ ---   ┆ ---                 ┆ ---  │
│ str      ┆ str               ┆ str           ┆ list[str] ┆   ┆ datetime[μs] ┆ i64   ┆ datetime[μs]        ┆ str  │
╞══════════╪═══════════════════╪═══════════════╪═══════════╪═══╪══════════════╪═══════╪═════════════════════╪══════╡
│ 1        ┆ Andersen, Hans    ┆ jn19990000171 ┆ ["aut"]   ┆ … ┆ 1953-01-01   ┆ 309   ┆ 1984-01-01 00:00:00 ┆ 252× │
│          ┆ Christian,        ┆               ┆           ┆   ┆ 00:00:00     ┆       ┆                     ┆      │
│ 1        ┆ Říha, Bohumil,    ┆ jk01110164    ┆ ["aut"]   ┆ … ┆ 2016-01-01   ┆ 84    ┆ 2005-01-01 00:00:00 ┆ 451× │
│          ┆                   ┆               ┆           ┆   ┆ 00:00:00     ┆       ┆                     ┆      │
│ 1        ┆ Lindgren, Astrid, ┆ jn19990005095 ┆ ["aut"]   ┆ … ┆ 2021-01-01   ┆ 275   ┆ null                ┆ 198× │
│          ┆                   ┆               ┆           ┆   ┆ 00:00:00     ┆       ┆                     ┆      │
└──────────┴───────────────────┴───────────────┴───────────┴───┴──────────────┴───────┴─────────────────────┴──────┘

In [142]:
base = alt.Chart(
    do_grafu2.filter(pl.col('700_a').is_in(nejaktivnejsi_ilustratori2)).to_pandas(), title=alt.TitleParams(
        f"{len(nejaktivnejsi_ilustratori2)} nejvydávanějších ilustrátorů a ilustrátorek",
    subtitle="Co tečka, to kniha. Černá čárka označuje rok úmrtí."))

kulicky = base.mark_circle(size=7, filled=True).encode(
            x=alt.X("rok:T", title=None, axis=alt.Axis(domainOpacity=0, tickColor='#DCDDD6')), 
            y=alt.Y("700_a:N", sort=nejaktivnejsi_ilustratori2, title=None, axis=alt.Axis(orient='left', domainOpacity=0, tickColor='white', labelExpr='split(datum.label, "× ")[1]' )), #, 
            yOffset=alt.YOffset("jitter:Q", scale=alt.Scale(range=[3, 15])), 
            color=alt.Color('700_a:N', scale=alt.Scale(range=['#E09DA3']), 
                            sort=nejaktivnejsi_ilustratori2).legend(None)) \
        .transform_calculate(jitter="sqrt(-2*log(random()))*cos(2*PI*random())")

kdy_umreli = base.mark_tick(
    color='#292829',  # optional: you can specify color
    thickness=1.5,
    height=9
).encode(
    x=alt.X('umrti:T', title=None),
    y=alt.Y("700_a:N", sort=nejaktivnejsi_ilustratori2, title=None, axis=alt.Axis(orient='left', tickColor='white', labels=False)))

pocty = base.mark_text().encode(x=alt.X('rok:T', title=None), 
    y=alt.Y('700_a:N', title=None, sort=nejaktivnejsi_ilustratori2, axis=alt.Axis(orient="right", tickColor='white', labelExpr='split(datum.label, " ")[0]'))) #

zebricek2 = alt.layer(kulicky, kdy_umreli, pocty).configure_view(stroke='transparent').properties(
    width=kredity['sirka'],
    autosize={'type': 'fit', 'contains': 'padding'}
).resolve_scale(color='independent',x="shared")

zebricek2

alt.LayerChart(...)

In [56]:
me_to_neurazi(zebricek2, kredity=kredity['default'], soubor='02_ilustratorstvo')

<figure>
    <a href="https://data.irozhlas.cz/knihy-grafy/02_ilustratorstvo.svg" target="_blank">
    <img src="https://data.irozhlas.cz/knihy-grafy/02_ilustratorstvo.svg" width="100%" alt="Omlouváme se, ale alternativní text se nepodařilo vygenerovat. Texty v grafu by měly být čitelné ze zdrojového souboru SVG." />
    </a>
    </figure>


In [57]:
df.filter(pl.col('700_a') == 'Born, Adolf,')

shape: (445, 68)
┌──────────┬───────────────────────────┬───────────────────┬────────────────┬───┬───────────┬───────────┬──────┬───────┐
│ 100_ind1 ┆ 100_a                     ┆ 100_7             ┆ 100_4          ┆ … ┆ 700_9     ┆ 700_g     ┆ rok  ┆ stran │
│ ---      ┆ ---                       ┆ ---               ┆ ---            ┆   ┆ ---       ┆ ---       ┆ ---  ┆ ---   │
│ str      ┆ str                       ┆ str               ┆ list[str]      ┆   ┆ list[str] ┆ list[str] ┆ i64  ┆ i64   │
╞══════════╪═══════════════════════════╪═══════════════════╪════════════════╪═══╪═══════════╪═══════════╪══════╪═══════╡
│ 1        ┆ Macourek, Miloš,          ┆ jk01072813        ┆ ["aut"]        ┆ … ┆ null      ┆ null      ┆ 2009 ┆ 110   │
│ 1        ┆ Muška, Ladislav,          ┆ jk01082552        ┆ ["aut"]        ┆ … ┆ null      ┆ null      ┆ 1962 ┆ 101   │
│ 1        ┆ Pecháček, Ladislav,       ┆ jk01092311        ┆ ["aut"]        ┆ … ┆ null      ┆ null      ┆ 2004 ┆ 115   │
│ 1        ┆ Slabý, Zdeněk Karel,      ┆ jk01111713        ┆ ["aut"]        ┆ … ┆ null      ┆ null      ┆ 1972 ┆ 30    │
│ 1        ┆ Čapek, Karel,             ┆ jk01021023        ┆ ["aut"]        ┆ … ┆ null      ┆ null      ┆ 1975 ┆ 92    │
│ 1        ┆ Kožík, František,         ┆ jk01062651        ┆ ["aut"]        ┆ … ┆ null      ┆ null      ┆ 1966 ┆ 70    │
│ 1        ┆ Krejčí, Stanislav         ┆ jk01063233        ┆ ["com", "trl"] ┆ … ┆ null      ┆ null      ┆ 1978 ┆ 94    │
│ 1        ┆ Žáček, Jiří,              ┆ jk01152946        ┆ ["aut"]        ┆ … ┆ null      ┆ null      ┆ 2015 ┆ 188   │
│ 1        ┆ Rolleczek, Natalia,       ┆ kup20020000083748 ┆ ["aut"]        ┆ … ┆ null      ┆ null      ┆ 1977 ┆ 106   │
│ 0        ┆ Lúkianos,                 ┆ jn19981001791     ┆ ["aut"]        ┆ … ┆ null      ┆ null      ┆ 1983 ┆ 222   │
│ 1        ┆ Říha, Bohumil,            ┆ jk01110164        ┆ ["aut"]        ┆ … ┆ null      ┆ null      ┆ 1977 ┆ 92    │
│ 1        ┆ Berger, Thomas,           ┆ jn20010310095     ┆ ["aut"]        ┆ … ┆ null      ┆ null      ┆ 1995 ┆ 444   │
│ 1        ┆ Frýbová, Zdena,           ┆ jk01032058        ┆ ["aut"]        ┆ … ┆ null      ┆ null      ┆ 2004 ┆ 237   │
│ 1        ┆ Horníček, Miroslav,       ┆ jk01042235        ┆ ["aut"]        ┆ … ┆ null      ┆ null      ┆ 1979 ┆ 249   │
│ 1        ┆ Borská, Ilona,            ┆ jk01012697        ┆ ["aut"]        ┆ … ┆ null      ┆ null      ┆ 1988 ┆ 159   │
│ 1        ┆ Wodehouse, P. G.          ┆ jn19990009232     ┆ ["aut"]        ┆ … ┆ null      ┆ null      ┆ 2008 ┆ 215   │
│ 1        ┆ Stehlíková, Blanka,       ┆ jk01121022        ┆ ["aut"]        ┆ … ┆ null      ┆ null      ┆ 1988 ┆ 134   │
│ 1        ┆ Šmíd, Zdeněk,             ┆ jn19990209873     ┆ ["aut"]        ┆ … ┆ null      ┆ null      ┆ 2004 ┆ 142   │
│ 1        ┆ Říha, Bohumil,            ┆ jk01110164        ┆ ["aut"]        ┆ … ┆ null      ┆ null      ┆ 2007 ┆ 176   │
│ 1        ┆ Franková, Hermína,        ┆ jk01031754        ┆ ["aut"]        ┆ … ┆ null      ┆ null      ┆ 1979 ┆ 147   │
│ 1        ┆ Macourek, Miloš,          ┆ jk01072813        ┆ ["aut"]        ┆ … ┆ null      ┆ null      ┆ 2000 ┆ 148   │
│ 1        ┆ Steklač, Vojtěch,         ┆ jk01121138        ┆ ["aut"]        ┆ … ┆ null      ┆ null      ┆ 2002 ┆ 184   │
│ 1        ┆ Drijverová, Martina,      ┆ jk01023067        ┆ ["aut"]        ┆ … ┆ null      ┆ null      ┆ 2019 ┆ 69    │
│ 1        ┆ Ulrich, Jindřich,         ┆ xx0076611         ┆ ["art"]        ┆ … ┆ null      ┆ null      ┆ 2010 ┆ 50    │
│ 1        ┆ Hartog, Jan de,           ┆ jn20000602818     ┆ ["aut"]        ┆ … ┆ null      ┆ null      ┆ 1983 ┆ 216   │
│ 1        ┆ Augusta, Pavel,           ┆ jk01010424        ┆ ["aut"]        ┆ … ┆ null      ┆ null      ┆ 1998 ┆ 176   │
│ 1        ┆ Lindgren, Astrid,         ┆ jn19990005095     ┆ ["aut"]        ┆ … ┆ null      ┆ null      ┆ 2014 ┆ 270   │
│ 1        ┆ Berger, Thomas,           ┆ jn20010310095     ┆ ["aut"]        ┆ … ┆ null      ┆ null      ┆ 1977 

In [58]:
df.filter(pl.col('700_4') == 'ill').group_by('700_a').agg(pl.col("245_a").n_unique()).sort(by="245_a",descending=True)

shape: (13_657, 2)
┌─────────────────────────────┬───────┐
│ 700_a                       ┆ 245_a │
│ ---                         ┆ ---   │
│ str                         ┆ u32   │
╞═════════════════════════════╪═══════╡
│ Born, Adolf,                ┆ 281   │
│ Burian, Zdeněk,             ┆ 230   │
│ Němeček, Jaroslav,          ┆ 179   │
│ Bouda, Cyril,               ┆ 166   │
│ Zmatlíková, Helena,         ┆ 164   │
│ Winter-Neprakta, Jiří,      ┆ 160   │
│ Krejčová, Zdeňka,           ┆ 159   │
│ Šplíchal, Antonín,          ┆ 143   │
│ Thuma, Karel Ladislav,      ┆ 134   │
│ Černý, Věnceslav,           ┆ 133   │
│ Vydrová, Markéta,           ┆ 128   │
│ Plicková, Edita,            ┆ 124   │
│ Svolinský, Karel,           ┆ 123   │
│ Študlarová, Zdeňka,         ┆ 122   │
│ Lada, Josef,                ┆ 122   │
│ Aleš, Mikoláš,              ┆ 119   │
│ Petráček, Jiří,             ┆ 108   │
│ Popprová, Andrea            ┆ 103   │
│ Lhoták, Kamil,              ┆ 99    │
│ Scheiner, Artuš,            ┆ 97    │
│ Slíva, Jiří,                ┆ 93    │
│ Jiránek, Vladimír,          ┆ 88    │
│ Trnka, Jiří,                ┆ 87    │
│ Janeček, Ota,               ┆ 85    │
│ Čuma, Aleš,                 ┆ 85    │
│ Hegerová, Vendula,          ┆ 84    │
│ Jakešová, Miroslava,        ┆ 84    │
│ Wowk, Jiří,                 ┆ 80    │
│ Schulz, Alena,              ┆ 80    │
│ Tesař, Vladimír,            ┆ 79    │
│ Fixl, Jiří,                 ┆ 78    │
│ Martenek, Miloslav,         ┆ 78    │
│ Velčovský, Josef,           ┆ 78    │
│ Čutta, Václav,              ┆ 76    │
│ Procházka, Otakar           ┆ 76    │
│ Kubašta, Vojtěch,           ┆ 75    │
│ Teissig, Karel,             ┆ 75    │
│ Kratochvíl, Zdeněk,         ┆ 74    │
│ Škoda, František,           ┆ 74    │
│ Komárek, Vladimír,          ┆ 73    │
│ Hora, Jan,                  ┆ 70    │
│ Kabát, Václav,              ┆ 70    │
│ Poppr, Roman                ┆ 68    │
│ Čapek, Josef,               ┆ 68    │
│ Renčín, Vladimír,           ┆ 68    │
│ Netopil, Zdeněk,            ┆ 66    │
│ Franta, Karel,              ┆ 66    │
│ Urban, Petr,                ┆ 66    │
│ Konůpek, Jan,               ┆ 65    │
│ Kalousek, Jiří,             ┆ 65    │
│ …                           ┆ …     │
│ Kostyra, Adam               ┆ 1     │
│ Oussedik, Marine,           ┆ 1     │
│ Schmidt, Georg              ┆ 1     │
│ Stankovianska, Jana,        ┆ 1     │
│ Chin Yew,                   ┆ 1     │
│ Berthou, Vincent,           ┆ 1     │
│ Hilbert, Petra,             ┆ 1     │
│ Harnden, Mike               ┆ 1     │
│ Franco, Paula               ┆ 1     │
│ Hudeček, Zdeněk,            ┆ 1     │
│ Mlejnková, Vlasta           ┆ 1     │
│ Schmaus-Shoonerová, Helena, ┆ 1     │
│ Manfroi, Patrizia           ┆ 1     │
│ Šmukař, Martin,             ┆ 1     │
│ Peška, Jan                  ┆ 1     │
│ Václavková, Olga,           ┆ 1     │
│ To, Marcus,                 ┆ 1     │
│ Ramsay, Stephen             ┆ 1     │
│ Žižka, Josef                ┆ 1     │
│ Puryear, Tony               ┆ 1     │
│ Hérenguel, Éric,            ┆ 1     │
│ Also,                       ┆ 1     │
│ Dvořák, Karel,              ┆ 1     │
│ Jurek, Vladimír             ┆ 1     │
│ Renčková Lesana, Veronika,  ┆ 1     │
│ Bartoněk, Vojtěch,          ┆ 1     │
│ Faberová, Věra              ┆ 1     │
│ Orecchia, Giulia            ┆ 1     │
│ Bucheli, Samuel,            ┆ 1     │
│ Kraus, Bohumil,             ┆ 1     │
│ Furukawa, Fernando Heinz,   ┆ 1     │
│ Mika, Cyril                 ┆ 1     │
│ Hála, Antonín,              ┆ 1     │
│ Růžová, Lucka               ┆ 1     │
│ Lüder, Rita,                ┆ 1     │
│ Kļaviņa, Līga,              ┆ 1     │
│ Hřivna, František,          ┆ 1     │
│ Kvítko, Vítek,              ┆ 1     │
│ Skálová, Jana               ┆ 1     │
│ Kafka, Vladimír,            ┆ 1     │
│ Susová, Michaela,           ┆ 1     │
│ Wears, Tony                 ┆ 1     │
│ Barnes-Murphy, Rowan,       ┆ 1     │
│ Verey, Tiras       

In [59]:
df_preklady = df.join(pl.read_parquet(os.path.join("data/cnb_sloupce","041.parquet")), left_on="001", right_on="001", how="left")

In [60]:
df_preklady.filter(pl.col('700_4') == 'trl').group_by('700_a').agg(pl.col("245_a").n_unique()).sort(by="245_a",descending=True)

shape: (18_202, 2)
┌────────────────────────────┬───────┐
│ 700_a                      ┆ 245_a │
│ ---                        ┆ ---   │
│ str                        ┆ u32   │
╞════════════════════════════╪═══════╡
│ Butala, Tomáš,             ┆ 502   │
│ Pavka, Marek,              ┆ 429   │
│ Vyskočil, Josef            ┆ 344   │
│ Sladká, Stanislava         ┆ 246   │
│ Schönová, Zuzana           ┆ 234   │
│ Volhejnová, Veronika,      ┆ 230   │
│ Podaný, Richard,           ┆ 224   │
│ Kuťák, Jaroslav,           ┆ 214   │
│ Chromiaková, Eva           ┆ 196   │
│ Pacnerová, Jana,           ┆ 195   │
│ Štorkánová, Anna,          ┆ 179   │
│ Klůfová, Petra,            ┆ 164   │
│ Jašová, Jana,              ┆ 163   │
│ Dušek, Zdík,               ┆ 155   │
│ Kadlecová, Eva,            ┆ 148   │
│ Pokorný, Martin,           ┆ 140   │
│ Řežábek, Rudolf,           ┆ 140   │
│ Lacinová, Libuše,          ┆ 140   │
│ Dvořáková, Dagmar          ┆ 134   │
│ Kantůrek, Jan,             ┆ 130   │
│ Smolaková, Helena          ┆ 127   │
│ Kozák, Jan,                ┆ 126   │
│ Sychra, Pavel              ┆ 122   │
│ Führmann Vízdalová, Ivana, ┆ 119   │
│ Jovanovičová, Hana,        ┆ 118   │
│ Stachová, Helena,          ┆ 117   │
│ Kufnerová, Zlata,          ┆ 117   │
│ Stach, Jiří,               ┆ 117   │
│ Škultéty, Michaela,        ┆ 112   │
│ Žáček, Milan,              ┆ 111   │
│ Niklíčková, Alexandra,     ┆ 109   │
│ Somogyi, Viola,            ┆ 107   │
│ Vlčková, Jana,             ┆ 107   │
│ Weinfurter, Karel,         ┆ 106   │
│ Diestlerová, Petra,        ┆ 104   │
│ Nuhlíčková, Ivana,         ┆ 102   │
│ Vinšová, Kateřina,         ┆ 102   │
│ Heller, František          ┆ 102   │
│ Krejčí, Hana               ┆ 102   │
│ Hradil, Radomil,           ┆ 99    │
│ Brožová, Eva               ┆ 98    │
│ Faltejsková, Lenka,        ┆ 98    │
│ Schuster, R. K.            ┆ 95    │
│ Morávková, Alena,          ┆ 93    │
│ Novotná, Jana,             ┆ 92    │
│ Chodilová, Dana,           ┆ 92    │
│ Žák, Jiří,                 ┆ 92    │
│ Rada, Jan                  ┆ 92    │
│ Zábrana, Jan,              ┆ 91    │
│ Křivánková, Anna,          ┆ 89    │
│ …                          ┆ …     │
│ Cekota, Petr,              ┆ 1     │
│ Hubík, Antonín             ┆ 1     │
│ Malík, Vratislav,          ┆ 1     │
│ Kapsa, Václav              ┆ 1     │
│ Pecharová, Klára           ┆ 1     │
│ Šrámek, Fráňa,             ┆ 1     │
│ Zentrich, Josef Antonín,   ┆ 1     │
│ Veselý, Adolf,             ┆ 1     │
│ Lund, Dana,                ┆ 1     │
│ Ženatý, Jan                ┆ 1     │
│ Husák, Ivan                ┆ 1     │
│ Doutlík, Miroslav,         ┆ 1     │
│ Pešková, Matylda,          ┆ 1     │
│ Pelikán, Robert,           ┆ 1     │
│ Durdík, Josef,             ┆ 1     │
│ Peňás, Josef               ┆ 1     │
│ Baum, Mirko,               ┆ 1     │
│ Kochanovská, Adéla,        ┆ 1     │
│ Michalská, Nora,           ┆ 1     │
│ Vitouš, Pavel,             ┆ 1     │
│ Pelikán, František X.      ┆ 1     │
│ Dumek, Josef,              ┆ 1     │
│ Bervicová, Marie           ┆ 1     │
│ Staňková, Ela              ┆ 1     │
│ Zelinská, Johana           ┆ 1     │
│ Lováková, Jiřina           ┆ 1     │
│ Stařík, Jiří               ┆ 1     │
│ Kohoutová, Jana            ┆ 1     │
│ Giorno, Dagmar             ┆ 1     │
│ Mašek, Gustav              ┆ 1     │
│ Aichlmanová, Alena         ┆ 1     │
│ Stril-Rever, Sofia         ┆ 1     │
│ Jurečka, Richard           ┆ 1     │
│ Zahradníková, Roxana       ┆ 1     │
│ Novotná, Jana              ┆ 1     │
│ Vaněčková, Renata          ┆ 1     │
│ Jílková, Helena            ┆ 1     │
│ Kolomý, Vojtěch            ┆ 1     │
│ Jakoubek, Marek,           ┆ 1     │
│ Mika, Karel,               ┆ 1     │
│ O'Rourke, Michael          ┆ 1     │
│ Balák, Jan Matěj,          ┆ 1     │
│ Trnka, Jakub               ┆ 1     │
│ Leckie, Jiřina,            ┆ 1     │
│ Trávníčková, Jana          ┆ 1     │
│ Vlasatý, Vladimír,         ┆ 1     │
│ J

In [61]:
df_preklady.filter(pl.col('700_a') == "Butala, Tomáš,").group_by("100_a").len()

shape: (33, 2)
┌────────────────────────────┬─────┐
│ 100_a                      ┆ len │
│ ---                        ┆ --- │
│ str                        ┆ u32 │
╞════════════════════════════╪═════╡
│ Murphy, Bill,              ┆ 10  │
│ Taylor, Kathryn            ┆ 3   │
│ Mortimer, Glenn            ┆ 4   │
│ Denver, Jeff,              ┆ 1   │
│ Roberts, Dan,              ┆ 1   │
│ Scott, William,            ┆ 141 │
│ Morton, Jack               ┆ 7   │
│ Aurel, Catherine,          ┆ 1   │
│ Morgan, Matt               ┆ 4   │
│ Engel, Cornelia            ┆ 1   │
│ Lane, Lex                  ┆ 4   │
│ Bellmar, Elena,            ┆ 2   │
│ Kutscher, Volker,          ┆ 10  │
│ Glaser, Frank              ┆ 9   │
│ Callahan, Frank            ┆ 2   │
│ Silva, Tony,               ┆ 1   │
│ Shannon, Mark              ┆ 1   │
│ Benson, Robert             ┆ 2   │
│ Czernin, Monika,           ┆ 1   │
│ Sharon, H. S.              ┆ 3   │
│ Warner, Hal,               ┆ 1   │
│ Sinclair, Luke             ┆ 8   │
│ Unger, Gert F.,            ┆ 391 │
│ Gringel, Dana,             ┆ 1   │
│ Schröder, Rainer M.,       ┆ 1   │
│ Fargo, Bill                ┆ 4   │
│ Schiewe, Ulf,              ┆ 1   │
│ Hayes, Rex,                ┆ 13  │
│ Arnaldur Indriðason,       ┆ 5   │
│ Goga-Klinkenberg, Susanne, ┆ 4   │
│ Robertson, Frank C.        ┆ 2   │
│ Vermalle, Caroline,        ┆ 1   │
│ Ryan, William              ┆ 4   │
└────────────────────────────┴─────┘

In [62]:
df_preklady.filter(pl.col('700_a') == "Butala, Tomáš,").group_by("041_h").len()

shape: (5, 2)
┌───────────┬─────┐
│ 041_h     ┆ len │
│ ---       ┆ --- │
│ list[str] ┆ u32 │
╞═══════════╪═════╡
│ ["eng"]   ┆ 3   │
│ ["ger"]   ┆ 633 │
│ ["ice"]   ┆ 5   │
│ ["fre"]   ┆ 1   │
│ null      ┆ 2   │
└───────────┴─────┘

In [63]:
df_preklady.filter(pl.col('700_4') == 'trl').group_by('700_a').agg(pl.col("245_a").n_unique()).sort(by="245_a",descending=True)

shape: (18_202, 2)
┌────────────────────────────┬───────┐
│ 700_a                      ┆ 245_a │
│ ---                        ┆ ---   │
│ str                        ┆ u32   │
╞════════════════════════════╪═══════╡
│ Butala, Tomáš,             ┆ 502   │
│ Pavka, Marek,              ┆ 429   │
│ Vyskočil, Josef            ┆ 344   │
│ Sladká, Stanislava         ┆ 246   │
│ Schönová, Zuzana           ┆ 234   │
│ Volhejnová, Veronika,      ┆ 230   │
│ Podaný, Richard,           ┆ 224   │
│ Kuťák, Jaroslav,           ┆ 214   │
│ Chromiaková, Eva           ┆ 196   │
│ Pacnerová, Jana,           ┆ 195   │
│ Štorkánová, Anna,          ┆ 179   │
│ Klůfová, Petra,            ┆ 164   │
│ Jašová, Jana,              ┆ 163   │
│ Dušek, Zdík,               ┆ 155   │
│ Kadlecová, Eva,            ┆ 148   │
│ Pokorný, Martin,           ┆ 140   │
│ Lacinová, Libuše,          ┆ 140   │
│ Řežábek, Rudolf,           ┆ 140   │
│ Dvořáková, Dagmar          ┆ 134   │
│ Kantůrek, Jan,             ┆ 130   │
│ Smolaková, Helena          ┆ 127   │
│ Kozák, Jan,                ┆ 126   │
│ Sychra, Pavel              ┆ 122   │
│ Führmann Vízdalová, Ivana, ┆ 119   │
│ Jovanovičová, Hana,        ┆ 118   │
│ Stach, Jiří,               ┆ 117   │
│ Stachová, Helena,          ┆ 117   │
│ Kufnerová, Zlata,          ┆ 117   │
│ Škultéty, Michaela,        ┆ 112   │
│ Žáček, Milan,              ┆ 111   │
│ Niklíčková, Alexandra,     ┆ 109   │
│ Somogyi, Viola,            ┆ 107   │
│ Vlčková, Jana,             ┆ 107   │
│ Weinfurter, Karel,         ┆ 106   │
│ Diestlerová, Petra,        ┆ 104   │
│ Heller, František          ┆ 102   │
│ Nuhlíčková, Ivana,         ┆ 102   │
│ Krejčí, Hana               ┆ 102   │
│ Vinšová, Kateřina,         ┆ 102   │
│ Hradil, Radomil,           ┆ 99    │
│ Faltejsková, Lenka,        ┆ 98    │
│ Brožová, Eva               ┆ 98    │
│ Schuster, R. K.            ┆ 95    │
│ Morávková, Alena,          ┆ 93    │
│ Chodilová, Dana,           ┆ 92    │
│ Žák, Jiří,                 ┆ 92    │
│ Rada, Jan                  ┆ 92    │
│ Novotná, Jana,             ┆ 92    │
│ Zábrana, Jan,              ┆ 91    │
│ Křivánková, Anna,          ┆ 89    │
│ …                          ┆ …     │
│ Hlaváčová, Alice           ┆ 1     │
│ Macháčková, Julie          ┆ 1     │
│ Švec, Karel,               ┆ 1     │
│ Bicek, Jaroslav,           ┆ 1     │
│ Hranická, Lucie            ┆ 1     │
│ Plouharová, Renáta         ┆ 1     │
│ Jírů, Roman,               ┆ 1     │
│ Pagač, Mojmír,             ┆ 1     │
│ Peřina, Vilém,             ┆ 1     │
│ Novotná, Drahomíra,        ┆ 1     │
│ Velechovská, Tereza        ┆ 1     │
│ Janotová, Nikola           ┆ 1     │
│ Passerin, Johana           ┆ 1     │
│ Kaplan, Aleš,              ┆ 1     │
│ Týmlová, Šárka,            ┆ 1     │
│ Nedvídek, Václav,          ┆ 1     │
│ Bosáková, Věra             ┆ 1     │
│ Pieczenik, Steve R.,       ┆ 1     │
│ Šícha, František           ┆ 1     │
│ Tomková, Marie             ┆ 1     │
│ Kusý, Jaroslav             ┆ 1     │
│ Nejedlá, Jaromíra,         ┆ 1     │
│ Kašpar, Jan Václav,        ┆ 1     │
│ Macek, Jaroslav,           ┆ 1     │
│ Černý, Rudolf,             ┆ 1     │
│ Šámal, Zdeněk,             ┆ 1     │
│ Ocisková, Marie            ┆ 1     │
│ Multrus, Vladimír          ┆ 1     │
│ Blažejová, Markéta,        ┆ 1     │
│ Čermák, Augustin           ┆ 1     │
│ Šuba, Pavel                ┆ 1     │
│ Puc, Jan                   ┆ 1     │
│ Smolanová, Jana            ┆ 1     │
│ Wohlmuthová, Iva           ┆ 1     │
│ Vondrášek, Karel,          ┆ 1     │
│ Hlinitý, Vincenc,          ┆ 1     │
│ Fiala, Vladimír            ┆ 1     │
│ Krejsa, Jan                ┆ 1     │
│ Greplová, Irena            ┆ 1     │
│ Rajmon, Jan                ┆ 1     │
│ Tomková, Ivana             ┆ 1     │
│ Macháček, David,           ┆ 1     │
│ Vávra, Josef,              ┆ 1     │
│ Oktábec, Vojtěch,          ┆ 1     │
│ Ladová, M.                 ┆ 1     │
│ Škrabánková, Anna          ┆ 1     │
│ H

In [64]:
df_preklady.filter(pl.col('700_4') == 'trl').group_by('700_a').agg(pl.col("stran").sum()).sort(by="stran",descending=True)

shape: (18_202, 2)
┌─────────────────────────────────┬────────┐
│ 700_a                           ┆ stran  │
│ ---                             ┆ ---    │
│ str                             ┆ i64    │
╞═════════════════════════════════╪════════╡
│ Volhejnová, Veronika,           ┆ 104086 │
│ Pacnerová, Jana,                ┆ 90284  │
│ Kantůrek, Jan,                  ┆ 80551  │
│ Podaný, Richard,                ┆ 76323  │
│ Dušek, Zdík,                    ┆ 68870  │
│ Jašová, Jana,                   ┆ 66951  │
│ Klůfová, Petra,                 ┆ 66769  │
│ Chodilová, Dana,                ┆ 56060  │
│ Medek, Pavel,                   ┆ 54195  │
│ Bartošková, Linda,              ┆ 53632  │
│ Řežábek, Rudolf,                ┆ 51852  │
│ Kobělka, Jiří,                  ┆ 50248  │
│ Pokorný, Martin,                ┆ 49472  │
│ Butala, Tomáš,                  ┆ 48256  │
│ Hron, Zdeněk,                   ┆ 45346  │
│ Zaorálek, Jaroslav,             ┆ 44751  │
│ Kotrle, Petr,                   ┆ 44222  │
│ Führmann Vízdalová, Ivana,      ┆ 43707  │
│ Krejčová, Dana                  ┆ 43672  │
│ Kozák, Jan,                     ┆ 43670  │
│ Faltejsková, Lenka,             ┆ 42989  │
│ Kadlecová, Eva,                 ┆ 42772  │
│ Trávníček, Luboš,               ┆ 42489  │
│ Kondrysová, Eva,                ┆ 41792  │
│ Ľalíková, Zuzana,               ┆ 41569  │
│ Žáček, Milan,                   ┆ 41130  │
│ Krištůfková, Kateřina,          ┆ 40202  │
│ Medek, Vladimír,                ┆ 39526  │
│ Jindrová, Alena,                ┆ 37979  │
│ Míček, Dalibor,                 ┆ 37961  │
│ Křivánková, Anna,               ┆ 37329  │
│ Trávníčková, Libuše,            ┆ 37257  │
│ Zábrana, Jan,                   ┆ 36956  │
│ Vlčková, Jana,                  ┆ 36700  │
│ Brožová, Eva                    ┆ 36699  │
│ Heller, František               ┆ 35764  │
│ Houbová, Věra,                  ┆ 35662  │
│ Moserová, Jaroslava,            ┆ 35535  │
│ Žák, Jiří,                      ┆ 35332  │
│ Weinfurter, Karel,              ┆ 34763  │
│ Stárková, Jiřina                ┆ 34565  │
│ Wolfová, Zora,                  ┆ 34555  │
│ Bičíková, Romana,               ┆ 34245  │
│ Křístková, Eva                  ┆ 34049  │
│ Nuhlíčková, Ivana,              ┆ 33785  │
│ Tilsch, Emanuel,                ┆ 33415  │
│ Marková, Michala,               ┆ 33354  │
│ Niklíčková, Alexandra,          ┆ 33232  │
│ Jindra, Miroslav,               ┆ 32742  │
│ Dvořák, Libor,                  ┆ 32490  │
│ …                               ┆ …      │
│ Raveane, Drahomíra              ┆ 1      │
│ Dyčková, Alžběta,               ┆ 1      │
│ Desenská Ciglerová, Jana        ┆ 1      │
│ Forejt, Matěj,                  ┆ 1      │
│ Velká, Tereza                   ┆ 1      │
│ Rudčenková, Kateřina,           ┆ 1      │
│ Malaník, Jiří                   ┆ 1      │
│ Piper, Erik,                    ┆ 1      │
│ Nguy, Giang Linh                ┆ 1      │
│ Marx, Jakub                     ┆ 1      │
│ Jezdinský, Jakub                ┆ 1      │
│ Maruščak, Marija Tarasivna      ┆ 1      │
│ Rohoža, Anna Vìktorìvna         ┆ 1      │
│ Berlad, Iryna Dmytrivna         ┆ 1      │
│ Majer, Petr,                    ┆ 1      │
│ Zavoral, Method Jan,            ┆ 1      │
│ Kursová, Veronika,              ┆ 1      │
│ Jelínek, Konstantin,            ┆ 1      │
│ Zoban, Petr,                    ┆ 1      │
│ Trnka, Jakub                    ┆ 1      │
│ Pavlisová, Hana                 ┆ 1      │
│ Vavruška, Jindřich              ┆ 1      │
│ Ponešová, Anita,                ┆ 1      │
│ Božek, Tomáš                    ┆ 1      │
│ Savčyn, Marìja-Mar'jana Volody… ┆ 1      │
│ Metličková, Kristýna            ┆ 1      │
│ Dudzik, Pavel                   ┆ 1      │
│ Malicki, Jarosław               ┆ 1      │
│ Kim, Mina                       ┆ 1      │
│ Paraiová, Pavlína               ┆ 1      │
│ Maršálek, Zdenko,               ┆ 1      │
│ Irena                           ┆ 1      │
│ Horníková, Pavlína 

In [65]:
df_preklady.filter(pl.col('700_a') == "Volhejnová, Veronika,").group_by("100_a").len().sort(by="len",descending=True)

shape: (106, 2)
┌────────────────────────┬─────┐
│ 100_a                  ┆ len │
│ ---                    ┆ --- │
│ str                    ┆ u32 │
╞════════════════════════╪═════╡
│ Kinney, Jeff,          ┆ 52  │
│ Christie, Agatha,      ┆ 29  │
│ Herbert, Frank,        ┆ 24  │
│ Walliams, David,       ┆ 21  │
│ Lewis, C. S.           ┆ 21  │
│ Green, John,           ┆ 17  │
│ Colfer, Chris,         ┆ 16  │
│ Le Carré, John,        ┆ 8   │
│ Morse, Brian,          ┆ 7   │
│ Hannah, Sophie,        ┆ 6   │
│ Grisham, John,         ┆ 6   │
│ Atkinson, Kate,        ┆ 5   │
│ Eason, Cassandra,      ┆ 5   │
│ Cunningham, Michael,   ┆ 5   │
│ Russell, Rachel Renée  ┆ 4   │
│ Clarke, Arthur C.      ┆ 4   │
│ Andrews, William W.    ┆ 4   │
│ Peters, Helen          ┆ 4   │
│ Daldry, Jeremy,        ┆ 4   │
│ Piers, Helen           ┆ 4   │
│ Colfer, Eoin,          ┆ 3   │
│ Smith, James,          ┆ 3   │
│ Herbert, Brian,        ┆ 3   │
│ Novik, Naomi,          ┆ 3   │
│ Allison, Jennifer,     ┆ 3   │
│ Asimov, Isaac,         ┆ 3   │
│ Anderson, Poul,        ┆ 3   │
│ Brown, Sandra,         ┆ 3   │
│ Lamb, Kathryn,         ┆ 3   │
│ Crichton, Michael,     ┆ 3   │
│ Barnes, Jennifer Lynn, ┆ 3   │
│ Smale, Holly,          ┆ 2   │
│ Mercree, Amy Leigh,    ┆ 2   │
│ Adeyemi, Tomi,         ┆ 2   │
│ Kaplický, Jan,         ┆ 2   │
│ Kalfař, Jaroslav,      ┆ 2   │
│ Thomson, Jamie,        ┆ 2   │
│ Levin, Ira,            ┆ 2   │
│ McKinlay, Deborah      ┆ 2   │
│ Johansen, Erika        ┆ 2   │
│ Twain, Mark,           ┆ 2   │
│ Chee, Traci            ┆ 2   │
│ Crouch, Blake,         ┆ 2   │
│ Rich, Roberta,         ┆ 2   │
│ George, Elizabeth,     ┆ 2   │
│ King, Andrew           ┆ 2   │
│ Donoghue, Emma,        ┆ 1   │
│ Levithan, David,       ┆ 1   │
│ Kostova, Elizabeth,    ┆ 1   │
│ Graham, Caroline,      ┆ 1   │
│ …                      ┆ …   │
│ Nelson, Jandy,         ┆ 1   │
│ Quirk, Lawrence J.,    ┆ 1   │
│ Arnold, Stephanie      ┆ 1   │
│ Jerome, Jerome K.      ┆ 1   │
│ Cornell, Paul,         ┆ 1   │
│ Durrant, Sabine        ┆ 1   │
│ Larwood, Kieran        ┆ 1   │
│ Kissick, Lucy          ┆ 1   │
│ Hedsel, Mark,          ┆ 1   │
│ Laurie, Meshel,        ┆ 1   │
│ Pollard, Michael,      ┆ 1   │
│ Anderson, Kevin J.,    ┆ 1   │
│ Silverberg, Robert,    ┆ 1   │
│ Moore, Alan,           ┆ 1   │
│ Shaheen, Michael A.    ┆ 1   │
│ Walls, Jeannette,      ┆ 1   │
│ La Fontaine, Jean de,  ┆ 1   │
│ Zhang, Amy,            ┆ 1   │
│ Poe, Edgar Allan,      ┆ 1   │
│ Piedilato, Janet       ┆ 1   │
│ Scott, Joanna,         ┆ 1   │
│ Matheson, Richard,     ┆ 1   │
│ Setterfield, Diane,    ┆ 1   │
│ Mendell, Adrienne      ┆ 1   │
│ Abrams, Stacey,        ┆ 1   │
│ Forleo, Marie          ┆ 1   │
│ Flinn, Alex,           ┆ 1   │
│ Cooper, Rose           ┆ 1   │
│ Marshall, David        ┆ 1   │
│ Selden, George,        ┆ 1   │
│ Garber, Joseph R.,     ┆ 1   │
│ Ross, JoAnn            ┆ 1   │
│ Josephs, Ray           ┆ 1   │
│ Reed, Henry,           ┆ 1   │
│ Kuttner, Henry,        ┆ 1   │
│ Kowitt, Holly          ┆ 1   │
│ Oula, Valerie          ┆ 1   │
│ Kvítek, Martin,        ┆ 1   │
│ Brooks, Kevin,         ┆ 1   │
│ Hubbard, L. Ron        ┆ 1   │
│ Extence, Gavin,        ┆ 1   │
│ Pessl, Marisha,        ┆ 1   │
│ Lee, Suh Yoon          ┆ 1   │
│ McIntyre, Anne,        ┆ 1   │
│ Winterson, Jeanette,   ┆ 1   │
│ Rennison, Louise,      ┆ 1   │
│ Hearne, Kevin,         ┆ 1   │
│ Koontz, Dean R.        ┆ 1   │
│ Michaels, Stase        ┆ 1   │
│ Neubauer, Bonnie       ┆ 1   │
└────────────────────────┴─────┘

In [66]:
df_preklady.explode("041_h").filter(pl.col('700_4') == 'trl').group_by('700_a').agg(pl.col("041_h").n_unique()).sort(by="041_h",descending=True)

shape: (18_202, 2)
┌────────────────────────────┬───────┐
│ 700_a                      ┆ 041_h │
│ ---                        ┆ ---   │
│ str                        ┆ u32   │
╞════════════════════════════╪═══════╡
│ Babler, Otto František,    ┆ 19    │
│ Hiršal, Josef,             ┆ 16    │
│ Vetti, O. S.,              ┆ 16    │
│ Vrchlický, Jaroslav,       ┆ 12    │
│ Bednář, Kamil,             ┆ 12    │
│ Žilina, Miloslav,          ┆ 11    │
│ Fischer, Otokar,           ┆ 11    │
│ Žáček, Jiří,               ┆ 11    │
│ Vladislav, Jan,            ┆ 11    │
│ Kosterka, Hugo,            ┆ 11    │
│ Sýs, Karel,                ┆ 11    │
│ Hrubín, František,         ┆ 10    │
│ Eisner, Pavel,             ┆ 10    │
│ Hackenschmied, Hanuš,      ┆ 9     │
│ Stankovský, Josef Jiří,    ┆ 9     │
│ Karpatský, Dušan,          ┆ 9     │
│ Štroblová, Jana,           ┆ 9     │
│ Borecký, Jaromír,          ┆ 9     │
│ Čvančara, Karel,           ┆ 8     │
│ Weinfurter, Karel,         ┆ 8     │
│ Novotný, Václav Juda,      ┆ 8     │
│ Vrbová, Hana,              ┆ 8     │
│ Vacek, Jindřich,           ┆ 8     │
│ Kundera, Ludvík,           ┆ 8     │
│ Vyskočil, Josef            ┆ 8     │
│ Pešková, Eliška,           ┆ 8     │
│ Zbavitel, Dušan,           ┆ 8     │
│ Mathesius, Bohumil,        ┆ 8     │
│ Závada, Vilém,             ┆ 8     │
│ Pelán, Jiří,               ┆ 8     │
│ Sládek, Josef Václav,      ┆ 8     │
│ Vrátný, Karel,             ┆ 8     │
│ Mertlík, Rudolf,           ┆ 8     │
│ Šádek, František,          ┆ 8     │
│ Kubišta, Luděk,            ┆ 8     │
│ Pokorný, Jaroslav,         ┆ 8     │
│ Somogyi, Viola,            ┆ 8     │
│ Renč, Václav,              ┆ 8     │
│ Koláček, Josef,            ┆ 7     │
│ Černý, Václav A.,          ┆ 7     │
│ Stříž, Antonín Ludvík,     ┆ 7     │
│ Nowak, Antonín,            ┆ 7     │
│ Hrůša, Josef,              ┆ 7     │
│ Bezděková, Eva,            ┆ 7     │
│ Kozák, Jan,                ┆ 7     │
│ Škultéty, Michaela,        ┆ 7     │
│ Peška, Bedřich,            ┆ 7     │
│ Frýbort, Zdeněk,           ┆ 7     │
│ Koněrza, Josef,            ┆ 7     │
│ Peisertová, Alena          ┆ 7     │
│ …                          ┆ …     │
│ Barth, Markéta             ┆ 1     │
│ Hrůza, Jiří,               ┆ 1     │
│ Boráková, Alena            ┆ 1     │
│ Eim, Vítězslav             ┆ 1     │
│ Páleníková, Eva            ┆ 1     │
│ Tišler, Tomáš              ┆ 1     │
│ Žofák, David               ┆ 1     │
│ Staněk, Eduard,            ┆ 1     │
│ Hoňková, Petra             ┆ 1     │
│ Klebes, Karel              ┆ 1     │
│ Goldberg, Alena            ┆ 1     │
│ Pavlíček, Petr             ┆ 1     │
│ Rákosníková, Jitka         ┆ 1     │
│ Ettlová, Veronika          ┆ 1     │
│ Nedělníková, Eva           ┆ 1     │
│ Cannavagio, Mariane        ┆ 1     │
│ Labaj, Emil                ┆ 1     │
│ Žemlová, Julie             ┆ 1     │
│ Říhová, Anna               ┆ 1     │
│ Hajný, Petr                ┆ 1     │
│ Hudec, Věroslav,           ┆ 1     │
│ Jettmar, Michael           ┆ 1     │
│ Volný, Petr                ┆ 1     │
│ Bernatová, Petra           ┆ 1     │
│ Marek, František Miloslav, ┆ 1     │
│ Smolíková, Eva             ┆ 1     │
│ Zajícová, Karolína         ┆ 1     │
│ Mlčoch, Tomáš,             ┆ 1     │
│ Lukešová, Libuše           ┆ 1     │
│ Boháč, Karel               ┆ 1     │
│ Vančura, Antonín,          ┆ 1     │
│ Syka, Jan                  ┆ 1     │
│ Chlupová, Marie            ┆ 1     │
│ Silvín, Jan                ┆ 1     │
│ Limburský, Richard,        ┆ 1     │
│ Hornát, Jaroslav,          ┆ 1     │
│ Burša, Jiří                ┆ 1     │
│ Svobodová, Marcela         ┆ 1     │
│ Szymik, Jan,               ┆ 1     │
│ Jangl, Ladislav,           ┆ 1     │
│ Vitíková, Michaela         ┆ 1     │
│ Brepta, Rudolf,            ┆ 1     │
│ Španihelová, Helena,       ┆ 1     │
│ Urbanová, Petra,           ┆ 1     │
│ Dombrovská, Petra          ┆ 1     │
│ Košťál, Antonín            ┆ 1     │
│ N

In [67]:
df_preklady.filter(pl.col('700_a') == "Babler, Otto František,").group_by('041_h').agg(pl.col("245_a").n_unique()).sort(by="245_a",descending=True)

shape: (20, 2)
┌─────────────────────────┬───────┐
│ 041_h                   ┆ 245_a │
│ ---                     ┆ ---   │
│ list[str]               ┆ u32   │
╞═════════════════════════╪═══════╡
│ ["eng"]                 ┆ 10    │
│ ["ger"]                 ┆ 9     │
│ ["fre"]                 ┆ 8     │
│ ["scr"]                 ┆ 5     │
│ null                    ┆ 5     │
│ ["hrv"]                 ┆ 3     │
│ ["ita"]                 ┆ 3     │
│ ["rus"]                 ┆ 2     │
│ ["bul"]                 ┆ 2     │
│ ["und"]                 ┆ 2     │
│ ["srp"]                 ┆ 2     │
│ ["lat"]                 ┆ 2     │
│ ["slv"]                 ┆ 1     │
│ ["lit"]                 ┆ 1     │
│ ["dut"]                 ┆ 1     │
│ ["fro"]                 ┆ 1     │
│ ["cze"]                 ┆ 1     │
│ ["fre", "eng"]          ┆ 1     │
│ ["pol"]                 ┆ 1     │
│ ["hrv", "slv", … "mac"] ┆ 1     │
└─────────────────────────┴───────┘

In [68]:
df_preklady.filter(pl.col('700_a') == "Hiršal, Josef,").group_by('041_h').agg(pl.col("245_a").n_unique()).sort(by="245_a",descending=True)

shape: (20, 2)
┌────────────────┬───────┐
│ 041_h          ┆ 245_a │
│ ---            ┆ ---   │
│ list[str]      ┆ u32   │
╞════════════════╪═══════╡
│ ["ger"]        ┆ 32    │
│ null           ┆ 12    │
│ ["por"]        ┆ 4     │
│ ["spa"]        ┆ 3     │
│ ["rum"]        ┆ 2     │
│ ["mul"]        ┆ 2     │
│ ["fre"]        ┆ 2     │
│ ["scr"]        ┆ 2     │
│ ["swe"]        ┆ 2     │
│ ["rus"]        ┆ 1     │
│ ["chi"]        ┆ 1     │
│ ["hrv"]        ┆ 1     │
│ ["hun"]        ┆ 1     │
│ ["por", "eng"] ┆ 1     │
│ ["per"]        ┆ 1     │
│ ["por", "fre"] ┆ 1     │
│ ["nor"]        ┆ 1     │
│ ["scc"]        ┆ 1     │
│ ["pal"]        ┆ 1     │
│ ["eng"]        ┆ 1     │
└────────────────┴───────┘